In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
import warnings
warnings.filterwarnings('ignore')
pd.options.display.max_columns = None
pd.options.display.max_rows = None
pd.options.display.float_format = '{:.6f}'.format
from sklearn.metrics import confusion_matrix,accuracy_score, f1_score, classification_report
from sklearn.metrics import roc_curve, roc_auc_score
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score,KFold

In [2]:
from sklearn.ensemble import AdaBoostClassifier, GradientBoostingClassifier
from xgboost import XGBClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB, BernoulliNB, MultinomialNB
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.pipeline import Pipeline
from sklearn.metrics import confusion_matrix,accuracy_score, f1_score, classification_report, precision_score, recall_score
from sklearn.model_selection import RandomizedSearchCV,StratifiedKFold
from catboost import CatBoostClassifier
from lightgbm import LGBMClassifier
from scipy.stats import randint as sp_randint
from scipy.stats import uniform as sp_uniform

In [3]:
df_new = pd.read_csv('no_show_new1.csv')

In [4]:
from sklearn.preprocessing import StandardScaler

df_num = df_new[['Age','Waitingperiod']]
df_cat = df_new.drop(['Age','Waitingperiod'],axis = 1)

ss = StandardScaler()

num_ss = ss.fit_transform(df_num)

df_num_ss = pd.DataFrame(num_ss, columns = df_num.columns)

df_new2 = pd.concat([df_num_ss, df_cat], axis = 1)

df_new2.head()

Age  Waitingperiod  Gender  Scholarship  Hipertension  Diabetes  \
0  0.763817      -0.715729       0     0.000000             1         0   
1  0.763817      -0.715729       1     0.000000             0         0   
2  1.027555      -0.715729       0     0.000000             0         0   
3 -1.346083      -0.715729       0     0.000000             0         0   
4  0.763817      -0.715729       0     0.000000             1         1   

   Alcoholism  Handcap  SMS_received  No-show  prior_appointments  \
0    0.000000 0.000000      0.000000        0            0.000000   
1    0.000000 0.000000      0.000000        0            1.000000   
2    0.000000 0.000000      0.000000        0            0.000000   
3    0.000000 0.000000      0.000000        0            1.000000   
4    0.000000 0.000000      0.000000        0            0.000000   

   regular_patient  prior_no_shows  Neighbourhood_Group1  \
0                0        0.000000                     0   
1                1        0.000000                     0   
2                0        0.000000                     1   
3                1        0.000000                     1   
4                0        0.000000                     0   

   Neighbourhood_Group2  Neighbourhood_Group3  Neighbourhood_Group4  \
0                     0                     1                     0   
1                     0                     1                     0   
2                     0                     0                     0   
3                     0                     0                     0   
4                     0                     1                     0   

   Neighbourhood_Group5  Neighbourhood_Group6  Neighbourhood_Group7  
0                     0                     0                     0  
1                     0                     0                     0  
2                     0                     0                     0  
3                     0                     0                     0  
4                     0                     0                     0

In [5]:
X = df_new2.drop('No-show', axis = 1)
y = df_new2['No-show']

X_train, X_test, y_train, y_test = train_test_split(X, y, random_state = 10, test_size = 0.3, stratify=y) 

In [6]:
params_lr = {'solver':['liblinear','newton-cg','lbfgs','sag','saga'],
          'penalty': ['none','l1','l2','elasticnet'],
         'C': [100,10,1.0,0.1,0.01]}

cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)

rsearch_lr = RandomizedSearchCV(estimator = LogisticRegression(), param_distributions = params_lr, n_iter = 100, cv = cv, scoring = 'f1_weighted', random_state = 42)

rsearch_lr.fit(X_train, y_train)

RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
                   estimator=LogisticRegression(), n_iter=100,
                   param_distributions={'C': [100, 10, 1.0, 0.1, 0.01],
                                        'penalty': ['none', 'l1', 'l2',
                                                    'elasticnet'],
                                        'solver': ['liblinear', 'newton-cg',
                                                   'lbfgs', 'sag', 'saga']},
                   random_state=42, scoring='f1_weighted')

In [7]:
rsearch_lr.best_params_

{'solver': 'saga', 'penalty': 'l2', 'C': 100}

In [8]:
lr_pipeline = Pipeline([
    ('lr_model', LogisticRegression(**rsearch_lr.best_params_))
])

In [9]:
params_dt = {'max_features':sp_randint(1,15),
          'max_depth': sp_randint(2,10),
         'min_samples_leaf': sp_randint(10,50),
         'criterion':['gini','entropy']}

cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)

rsearch_dt = RandomizedSearchCV(estimator = DecisionTreeClassifier(random_state = 42), param_distributions = params_dt, n_iter = 100, cv = cv, scoring = 'f1_weighted', random_state = 42)

rsearch_dt.fit(X_train, y_train)

RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
                   estimator=DecisionTreeClassifier(random_state=42),
                   n_iter=100,
                   param_distributions={'criterion': ['gini', 'entropy'],
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027C2CC16430>,
                                        'max_features': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027C2CC2D340>,
                                        'min_samples_leaf': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027C2CC43040>},
                   random_state=42, scoring='f1_weighted')

In [10]:
rsearch_dt.best_params_

{'criterion': 'gini',
 'max_depth': 9,
 'max_features': 13,
 'min_samples_leaf': 27}

In [11]:
dt_pipeline = Pipeline([
    ('dt_model', DecisionTreeClassifier(**rsearch_dt.best_params_,random_state=42))
])

In [12]:
params_rf = {'n_estimators':sp_randint(50,150),
          'max_features':sp_randint(1,15),
          'max_depth': sp_randint(2,10),
         'min_samples_leaf': sp_randint(10,50),
         'criterion':['gini','entropy']}

cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)

rsearch_rf = RandomizedSearchCV(estimator = RandomForestClassifier(random_state = 42), param_distributions = params_rf, n_iter = 100, cv = cv, scoring = 'f1_weighted', random_state = 42)

rsearch_rf.fit(X_train, y_train)

RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
                   estimator=RandomForestClassifier(random_state=42),
                   n_iter=100,
                   param_distributions={'criterion': ['gini', 'entropy'],
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027C2CC217C0>,
                                        'max_features': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027C2CC35790>,
                                        'min_samples_leaf': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027C2CC3BCA0>,
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027C2CC213A0>},
                   random_state=42, scoring='f1_weighted')

In [13]:
rsearch_rf.best_params_

{'criterion': 'entropy',
 'max_depth': 9,
 'max_features': 8,
 'min_samples_leaf': 16,
 'n_estimators': 116}

In [14]:
rf_pipeline = Pipeline([
    ('rf_model', RandomForestClassifier(**rsearch_rf.best_params_,random_state=42))
])

In [15]:
gnb_pipeline = Pipeline([
    ('gnb_model', GaussianNB())
])

In [16]:
bnb_pipeline = Pipeline([
    ('bnb_model', BernoulliNB())
])

In [17]:
knn_pipeline = Pipeline([
    ('knn_model', KNeighborsClassifier())
])

In [18]:
params_ada = {'n_estimators':sp_randint(20,150),
          'learning_rate':[0.0001,0.001,0.01,0.1,1,2,3,4,5]}

cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)

rsearch_ada = RandomizedSearchCV(estimator = AdaBoostClassifier(random_state = 42), param_distributions = params_ada, n_iter = 100, cv = cv, scoring = 'f1_weighted', random_state = 42)

rsearch_ada.fit(X_train, y_train)

RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
                   estimator=AdaBoostClassifier(random_state=42), n_iter=100,
                   param_distributions={'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1, 2, 3, 4, 5],
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027C2CC00EE0>},
                   random_state=42, scoring='f1_weighted')

In [19]:
rsearch_ada.best_params_

{'learning_rate': 1, 'n_estimators': 101}

In [20]:
ada_pipeline = Pipeline([
    ('rf_model', AdaBoostClassifier(**rsearch_ada.best_params_, random_state = 42))
])

In [21]:
params_gb = {'n_estimators':sp_randint(50,200),
          'max_features':sp_randint(1,15),
          'max_depth': sp_randint(2,10),
         'learning_rate':[0.0001,0.001,0.01,0.1,1,2,3,4,5]}

cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)

rsearch_gb = RandomizedSearchCV(estimator = GradientBoostingClassifier(random_state = 42), param_distributions = params_gb, n_iter = 100, cv = cv, scoring = 'f1_weighted', random_state = 42)

rsearch_gb.fit(X_train, y_train)

RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
                   estimator=GradientBoostingClassifier(random_state=42),
                   n_iter=100,
                   param_distributions={'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1, 2, 3, 4, 5],
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027C2CC94D30>,
                                        'max_features': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027C2CC4BC70>,
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027C2F7057C0>},
                   random_state=42, scoring='f1_weighted')

In [22]:
rsearch_gb.best_params_

{'learning_rate': 0.1, 'max_depth': 2, 'max_features': 12, 'n_estimators': 63}

In [23]:
gb_pipeline = Pipeline([
    ('rf_model', GradientBoostingClassifier(**rsearch_gb.best_params_, random_state = 42))
])

In [24]:
params_cb = {'n_estimators':sp_randint(50,200),
          'max_depth': sp_randint(2,10),
         'learning_rate':[0.0001,0.001,0.01,0.1]}

cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)

rsearch_cb = RandomizedSearchCV(estimator = CatBoostClassifier(random_state = 42), param_distributions = params_cb, n_iter = 100, cv = cv, scoring = 'f1_weighted', random_state = 42)

rsearch_cb.fit(X_train, y_train)

0:	learn: 0.6885522	total: 139ms	remaining: 19.6s
1:	learn: 0.6840265	total: 142ms	remaining: 9.94s
2:	learn: 0.6795166	total: 145ms	remaining: 6.71s
3:	learn: 0.6751380	total: 148ms	remaining: 5.09s
4:	learn: 0.6707701	total: 150ms	remaining: 4.12s
5:	learn: 0.6666401	total: 153ms	remaining: 3.47s
6:	learn: 0.6624708	total: 156ms	remaining: 3s
7:	learn: 0.6584190	total: 158ms	remaining: 2.65s
8:	learn: 0.6543823	total: 161ms	remaining: 2.37s
9:	learn: 0.6505256	total: 163ms	remaining: 2.15s
10:	learn: 0.6466649	total: 166ms	remaining: 1.98s
11:	learn: 0.6429116	total: 169ms	remaining: 1.82s
12:	learn: 0.6392917	total: 171ms	remaining: 1.7s
13:	learn: 0.6356499	total: 174ms	remaining: 1.59s
14:	learn: 0.6320576	total: 176ms	remaining: 1.49s
15:	learn: 0.6285250	total: 179ms	remaining: 1.41s
16:	learn: 0.6250741	total: 182ms	remaining: 1.33s
17:	learn: 0.6216254	total: 184ms	remaining: 1.27s
18:	learn: 0.6183389	total: 187ms	remaining: 1.21s
19:	learn: 0.6150838	total: 189ms	remaining: 

67:	learn: 0.5096852	total: 180ms	remaining: 195ms
68:	learn: 0.5082119	total: 182ms	remaining: 193ms
69:	learn: 0.5067429	total: 185ms	remaining: 190ms
70:	learn: 0.5053643	total: 187ms	remaining: 187ms
71:	learn: 0.5039828	total: 190ms	remaining: 185ms
72:	learn: 0.5026250	total: 192ms	remaining: 182ms
73:	learn: 0.5013070	total: 195ms	remaining: 179ms
74:	learn: 0.4999632	total: 197ms	remaining: 176ms
75:	learn: 0.4986670	total: 200ms	remaining: 173ms
76:	learn: 0.4973433	total: 202ms	remaining: 171ms
77:	learn: 0.4960973	total: 205ms	remaining: 168ms
78:	learn: 0.4948553	total: 207ms	remaining: 165ms
79:	learn: 0.4936422	total: 210ms	remaining: 162ms
80:	learn: 0.4924260	total: 212ms	remaining: 160ms
81:	learn: 0.4912761	total: 215ms	remaining: 157ms
82:	learn: 0.4901038	total: 217ms	remaining: 154ms
83:	learn: 0.4890477	total: 220ms	remaining: 152ms
84:	learn: 0.4879195	total: 222ms	remaining: 149ms
85:	learn: 0.4867944	total: 224ms	remaining: 146ms
86:	learn: 0.4857400	total: 227

139:	learn: 0.4454902	total: 366ms	remaining: 5.23ms
140:	learn: 0.4450193	total: 369ms	remaining: 2.61ms
141:	learn: 0.4445114	total: 371ms	remaining: 0us
0:	learn: 0.6885275	total: 3.55ms	remaining: 501ms
1:	learn: 0.6840095	total: 7.37ms	remaining: 516ms
2:	learn: 0.6795149	total: 9.97ms	remaining: 462ms
3:	learn: 0.6751484	total: 12.6ms	remaining: 435ms
4:	learn: 0.6707922	total: 15.3ms	remaining: 419ms
5:	learn: 0.6666315	total: 17.9ms	remaining: 406ms
6:	learn: 0.6624751	total: 20.4ms	remaining: 394ms
7:	learn: 0.6583787	total: 22.9ms	remaining: 384ms
8:	learn: 0.6543657	total: 25.5ms	remaining: 377ms
9:	learn: 0.6505185	total: 28.1ms	remaining: 370ms
10:	learn: 0.6466724	total: 30.9ms	remaining: 367ms
11:	learn: 0.6429231	total: 33.6ms	remaining: 364ms
12:	learn: 0.6393116	total: 36.3ms	remaining: 360ms
13:	learn: 0.6356826	total: 38.9ms	remaining: 356ms
14:	learn: 0.6321054	total: 41.5ms	remaining: 351ms
15:	learn: 0.6286286	total: 44ms	remaining: 347ms
16:	learn: 0.6251886	tot

69:	learn: 0.5066697	total: 183ms	remaining: 189ms
70:	learn: 0.5052903	total: 186ms	remaining: 186ms
71:	learn: 0.5038776	total: 189ms	remaining: 183ms
72:	learn: 0.5025190	total: 191ms	remaining: 181ms
73:	learn: 0.5012007	total: 194ms	remaining: 178ms
74:	learn: 0.4998512	total: 196ms	remaining: 175ms
75:	learn: 0.4985551	total: 199ms	remaining: 173ms
76:	learn: 0.4972372	total: 202ms	remaining: 170ms
77:	learn: 0.4960288	total: 204ms	remaining: 168ms
78:	learn: 0.4947892	total: 207ms	remaining: 165ms
79:	learn: 0.4935750	total: 210ms	remaining: 163ms
80:	learn: 0.4923623	total: 212ms	remaining: 160ms
81:	learn: 0.4912099	total: 215ms	remaining: 157ms
82:	learn: 0.4900398	total: 217ms	remaining: 154ms
83:	learn: 0.4889830	total: 220ms	remaining: 152ms
84:	learn: 0.4878613	total: 222ms	remaining: 149ms
85:	learn: 0.4867298	total: 225ms	remaining: 147ms
86:	learn: 0.4856771	total: 228ms	remaining: 144ms
87:	learn: 0.4845455	total: 230ms	remaining: 141ms
88:	learn: 0.4834562	total: 233

0:	learn: 0.6885180	total: 2.9ms	remaining: 348ms
1:	learn: 0.6839477	total: 5.76ms	remaining: 343ms
2:	learn: 0.6795848	total: 8.13ms	remaining: 320ms
3:	learn: 0.6751941	total: 10.5ms	remaining: 308ms
4:	learn: 0.6709671	total: 12.8ms	remaining: 297ms
5:	learn: 0.6667514	total: 15ms	remaining: 287ms
6:	learn: 0.6626410	total: 17.3ms	remaining: 281ms
7:	learn: 0.6585696	total: 19.5ms	remaining: 275ms
8:	learn: 0.6546248	total: 21.7ms	remaining: 271ms
9:	learn: 0.6507468	total: 24ms	remaining: 267ms
10:	learn: 0.6469036	total: 26.2ms	remaining: 262ms
11:	learn: 0.6431642	total: 28.4ms	remaining: 258ms
12:	learn: 0.6394944	total: 30.7ms	remaining: 255ms
13:	learn: 0.6359210	total: 32.9ms	remaining: 252ms
14:	learn: 0.6323440	total: 35.2ms	remaining: 249ms
15:	learn: 0.6288739	total: 37.5ms	remaining: 246ms
16:	learn: 0.6254227	total: 39.9ms	remaining: 244ms
17:	learn: 0.6221432	total: 42.2ms	remaining: 242ms
18:	learn: 0.6188333	total: 44.5ms	remaining: 239ms
19:	learn: 0.6156716	total:

...

0:	learn: 0.6492968	total: 12.6ms	remaining: 2.36s
1:	learn: 0.6123923	total: 16.8ms	remaining: 1.57s
2:	learn: 0.5820027	total: 27.5ms	remaining: 1.71s
3:	learn: 0.5572744	total: 42.8ms	remaining: 1.98s
4:	learn: 0.5353606	total: 46.9ms	remaining: 1.73s
5:	learn: 0.5171169	total: 57.9ms	remaining: 1.76s
6:	learn: 0.5015037	total: 89.5ms	remaining: 2.33s
7:	learn: 0.4886850	total: 93.4ms	remaining: 2.11s
8:	learn: 0.4775790	total: 121ms	remaining: 2.41s
9:	learn: 0.4676848	total: 125ms	remaining: 2.23s
10:	learn: 0.4596751	total: 135ms	remaining: 2.18s
11:	learn: 0.4519885	total: 151ms	remaining: 2.23s
12:	learn: 0.4456581	total: 167ms	remaining: 2.26s
13:	learn: 0.4402655	total: 171ms	remaining: 2.13s
14:	learn: 0.4356073	total: 181ms	remaining: 2.1s
15:	learn: 0.4318056	total: 197ms	remaining: 2.13s
16:	learn: 0.4281375	total: 201ms	remaining: 2.04s
17:	learn: 0.4252084	total: 220ms	remaining: 2.09s
18:	learn: 0.4225266	total: 224ms	remaining: 2s
19:	learn: 0.4200151	total: 235ms	rem

162:	learn: 0.3953877	total: 1.8s	remaining: 287ms
163:	learn: 0.3953168	total: 1.82s	remaining: 277ms
164:	learn: 0.3952622	total: 1.82s	remaining: 265ms
165:	learn: 0.3951945	total: 1.83s	remaining: 253ms
166:	learn: 0.3951506	total: 1.85s	remaining: 244ms
167:	learn: 0.3950885	total: 1.85s	remaining: 232ms
168:	learn: 0.3950655	total: 1.86s	remaining: 221ms
169:	learn: 0.3950073	total: 1.88s	remaining: 210ms
170:	learn: 0.3949606	total: 1.89s	remaining: 198ms
171:	learn: 0.3949240	total: 1.9s	remaining: 187ms
172:	learn: 0.3948771	total: 1.91s	remaining: 177ms
173:	learn: 0.3948012	total: 1.93s	remaining: 166ms
174:	learn: 0.3947545	total: 1.93s	remaining: 155ms
175:	learn: 0.3947013	total: 1.94s	remaining: 143ms
176:	learn: 0.3946665	total: 1.96s	remaining: 133ms
177:	learn: 0.3946230	total: 1.96s	remaining: 121ms
178:	learn: 0.3945816	total: 1.97s	remaining: 110ms
179:	learn: 0.3945153	total: 1.99s	remaining: 99.4ms
180:	learn: 0.3945029	total: 2.01s	remaining: 88.9ms
181:	learn: 

38:	learn: 0.6913278	total: 199ms	remaining: 96.9ms
39:	learn: 0.6912823	total: 219ms	remaining: 98.4ms
40:	learn: 0.6912347	total: 222ms	remaining: 92ms
41:	learn: 0.6911891	total: 225ms	remaining: 85.7ms
42:	learn: 0.6911418	total: 233ms	remaining: 81.4ms
43:	learn: 0.6910957	total: 236ms	remaining: 75.1ms
44:	learn: 0.6910509	total: 239ms	remaining: 69ms
45:	learn: 0.6910040	total: 242ms	remaining: 63.1ms
46:	learn: 0.6909573	total: 245ms	remaining: 57.3ms
47:	learn: 0.6909125	total: 248ms	remaining: 51.7ms
48:	learn: 0.6908637	total: 264ms	remaining: 48.5ms
49:	learn: 0.6908186	total: 268ms	remaining: 42.8ms
50:	learn: 0.6907716	total: 271ms	remaining: 37.2ms
51:	learn: 0.6907244	total: 274ms	remaining: 31.6ms
52:	learn: 0.6906789	total: 277ms	remaining: 26.1ms
53:	learn: 0.6906309	total: 280ms	remaining: 20.7ms
54:	learn: 0.6905855	total: 283ms	remaining: 15.4ms
55:	learn: 0.6905394	total: 286ms	remaining: 10.2ms
56:	learn: 0.6904931	total: 289ms	remaining: 5.07ms
57:	learn: 0.690

61:	learn: 0.4039630	total: 180ms	remaining: 276ms
62:	learn: 0.4038947	total: 183ms	remaining: 273ms
63:	learn: 0.4038288	total: 186ms	remaining: 270ms
64:	learn: 0.4037581	total: 189ms	remaining: 267ms
65:	learn: 0.4037145	total: 191ms	remaining: 264ms
66:	learn: 0.4036216	total: 194ms	remaining: 261ms
67:	learn: 0.4035755	total: 197ms	remaining: 258ms
68:	learn: 0.4035212	total: 200ms	remaining: 255ms
69:	learn: 0.4034798	total: 203ms	remaining: 252ms
70:	learn: 0.4033830	total: 206ms	remaining: 249ms
71:	learn: 0.4033378	total: 209ms	remaining: 246ms
72:	learn: 0.4033087	total: 211ms	remaining: 243ms
73:	learn: 0.4032507	total: 214ms	remaining: 240ms
74:	learn: 0.4032165	total: 217ms	remaining: 237ms
75:	learn: 0.4031809	total: 219ms	remaining: 234ms
76:	learn: 0.4031480	total: 222ms	remaining: 231ms
77:	learn: 0.4031134	total: 225ms	remaining: 228ms
78:	learn: 0.4030606	total: 228ms	remaining: 225ms
79:	learn: 0.4030281	total: 231ms	remaining: 222ms
80:	learn: 0.4029850	total: 234

RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
                   estimator=<catboost.core.CatBoostClassifier object at 0x0000027C2CC99F70>,
                   n_iter=100,
                   param_distributions={'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1],
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027C2CCDE310>,
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027C2CC99E80>},
                   random_state=42, scoring='f1_weighted')

In [25]:
rsearch_cb.best_params_

{'learning_rate': 0.1, 'max_depth': 5, 'n_estimators': 157}

In [26]:
cb_pipeline = Pipeline([
    ('cb_model', CatBoostClassifier(**rsearch_cb.best_params_, random_state = 42))
])

In [27]:
params_lgbm = {'n_estimators':sp_randint(50,200),
          'num_leaves':sp_randint(2,50),
          'max_depth': sp_randint(2,10),
         'learning_rate':[0.0001,0.001,0.01,0.1,1,2,3,4,5]}

cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)

rsearch_lgbm = RandomizedSearchCV(estimator = LGBMClassifier(random_state = 42), param_distributions = params_lgbm, n_iter = 100, cv = cv, scoring = 'f1_weighted', random_state = 42)

rsearch_lgbm.fit(X_train, y_train)

RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
                   estimator=LGBMClassifier(random_state=42), n_iter=100,
                   param_distributions={'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1, 2, 3, 4, 5],
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027C2CC96400>,
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027C2F73C670>,
                                        'num_leaves': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027C2CC005E0>},
                   random_state=42, scoring='f1_weighted')

In [28]:
rsearch_lgbm.best_params_

{'learning_rate': 0.1, 'max_depth': 7, 'n_estimators': 96, 'num_leaves': 36}

In [29]:
lgbm_pipeline = Pipeline([
    ('lgbm_model', LGBMClassifier(**rsearch_lgbm.best_params_, random_state = 42))
])

In [30]:
params_xgb = {'gamma':sp_randint(0,5),
          'max_depth': sp_randint(2,10),
         'learning_rate':[0.0001,0.001,0.01,0.1,1,2,3,4,5]}

cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)

rsearch_xgb = RandomizedSearchCV(estimator = XGBClassifier(random_state = 42), param_distributions = params_xgb, n_iter = 100, cv = cv, scoring = 'f1_weighted', random_state = 42)

rsearch_xgb.fit(X_train, y_train)

RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
                   estimator=XGBClassifier(base_score=None, booster=None,
                                           callbacks=None,
                                           colsample_bylevel=None,
                                           colsample_bynode=None,
                                           colsample_bytree=None,
                                           early_stopping_rounds=None,
                                           enable_categorical=False,
                                           eval_metric=None, gamma=None,
                                           gpu_id=None, grow_policy=None,
                                           importance_type=None,
                                           intera...
                                           predictor=None, random_state=42,
                                           reg_alpha=None, reg_lambda=None, ...),
                   n_it

In [31]:
rsearch_xgb.best_params_

{'gamma': 2, 'learning_rate': 1, 'max_depth': 3}

In [32]:
xgb_pipeline = Pipeline([
    ('rf_model', XGBClassifier(**rsearch_xgb.best_params_, random_state = 42))
])

In [33]:
pipe_all = [lr_pipeline, dt_pipeline, rf_pipeline, gnb_pipeline, bnb_pipeline, ada_pipeline, gb_pipeline, xgb_pipeline, cb_pipeline, lgbm_pipeline,
            knn_pipeline]

for pipe in pipe_all:
  pipe.fit(X_train, y_train)

0:	learn: 0.6493197	total: 3.73ms	remaining: 581ms
1:	learn: 0.6132863	total: 6.98ms	remaining: 541ms
2:	learn: 0.5827405	total: 10ms	remaining: 515ms
3:	learn: 0.5577868	total: 13ms	remaining: 499ms
4:	learn: 0.5361193	total: 16.1ms	remaining: 491ms
5:	learn: 0.5187599	total: 19.1ms	remaining: 481ms
6:	learn: 0.5034772	total: 22.1ms	remaining: 474ms
7:	learn: 0.4906715	total: 25.3ms	remaining: 472ms
8:	learn: 0.4793150	total: 28.4ms	remaining: 467ms
9:	learn: 0.4698993	total: 31.5ms	remaining: 463ms
10:	learn: 0.4613321	total: 34.6ms	remaining: 460ms
11:	learn: 0.4542151	total: 37.7ms	remaining: 455ms
12:	learn: 0.4483692	total: 40.7ms	remaining: 451ms
13:	learn: 0.4436694	total: 43.6ms	remaining: 446ms
14:	learn: 0.4389387	total: 46.8ms	remaining: 443ms
15:	learn: 0.4349779	total: 49.5ms	remaining: 436ms
16:	learn: 0.4314222	total: 52.3ms	remaining: 431ms
17:	learn: 0.4280650	total: 55.1ms	remaining: 425ms
18:	learn: 0.4258781	total: 58ms	remaining: 422ms
19:	learn: 0.4236398	total: 

In [34]:
model_scores = {"Model Name" : [],
    'Accuracy train': [], 'Precision train': [], 'Recall train': [], 'F1 train': [], 'F1 Avg Weighted train' : [], 'ROC AUC train': [],
    'Accuracy test': [], 'Precision test': [], 'Recall test': [], 'F1 test': [], 'F1 Avg Weighted test' : [], 'ROC AUC test': [], 
                'CV-5-Mean': [], 'CV-5-SD': []}

for model in pipe_all:
    
    model_scores['Model Name'].append(str(model[0]).split('(')[0])
    
    model_scores['Accuracy train'].append(model.score(X_train, y_train))
    pred_tr = model.predict(X_train)
    prob_tr = model.predict_proba(X_train)[:,1]
    model_scores['Precision train'].append(precision_score(y_train, pred_tr))
    model_scores['Recall train'].append(recall_score(y_train, pred_tr))
    model_scores['F1 train'].append(f1_score(y_train, pred_tr))
    model_scores['F1 Avg Weighted train'].append(f1_score(y_train, pred_tr, average = 'weighted'))
    model_scores['ROC AUC train'].append(roc_auc_score(y_train, prob_tr))
    
    model_scores['Accuracy test'].append(model.score(X_test, y_test))
    pred_ts = model.predict(X_test)
    prob_ts = model.predict_proba(X_test)[:,1]
    model_scores['Precision test'].append(precision_score(y_test, pred_ts))
    model_scores['Recall test'].append(recall_score(y_test, pred_ts))
    model_scores['F1 test'].append(f1_score(y_test, pred_ts))
    model_scores['F1 Avg Weighted test'].append(f1_score(y_test, pred_ts, average = 'weighted'))
    model_scores['ROC AUC test'].append(roc_auc_score(y_test, prob_ts))

    model_scores['CV-5-Mean'].append(cross_val_score(model,X_train,y_train,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').mean())
    model_scores['CV-5-SD'].append(cross_val_score(model,X_train,y_train,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').std())

0:	learn: 0.6491593	total: 14.7ms	remaining: 2.29s
1:	learn: 0.6129849	total: 17.7ms	remaining: 1.37s
2:	learn: 0.5824683	total: 20.1ms	remaining: 1.03s
3:	learn: 0.5573919	total: 22.9ms	remaining: 874ms
4:	learn: 0.5359689	total: 25.5ms	remaining: 776ms
5:	learn: 0.5185750	total: 28.3ms	remaining: 712ms
6:	learn: 0.5030374	total: 30.9ms	remaining: 661ms
7:	learn: 0.4901561	total: 33.4ms	remaining: 623ms
8:	learn: 0.4785717	total: 36.1ms	remaining: 593ms
9:	learn: 0.4689968	total: 38.6ms	remaining: 567ms
10:	learn: 0.4603929	total: 41.2ms	remaining: 547ms
11:	learn: 0.4534230	total: 43.8ms	remaining: 530ms
12:	learn: 0.4470251	total: 46.6ms	remaining: 516ms
13:	learn: 0.4419375	total: 49.1ms	remaining: 502ms
14:	learn: 0.4373062	total: 51.7ms	remaining: 489ms
15:	learn: 0.4332042	total: 54.1ms	remaining: 477ms
16:	learn: 0.4293008	total: 56.8ms	remaining: 467ms
17:	learn: 0.4263705	total: 59.3ms	remaining: 458ms
18:	learn: 0.4241756	total: 62ms	remaining: 450ms
19:	learn: 0.4220347	tot

73:	learn: 0.4020365	total: 199ms	remaining: 223ms
74:	learn: 0.4019972	total: 202ms	remaining: 221ms
75:	learn: 0.4019339	total: 204ms	remaining: 218ms
76:	learn: 0.4019071	total: 207ms	remaining: 215ms
77:	learn: 0.4018617	total: 210ms	remaining: 213ms
78:	learn: 0.4017712	total: 213ms	remaining: 210ms
79:	learn: 0.4017186	total: 216ms	remaining: 208ms
80:	learn: 0.4016711	total: 218ms	remaining: 205ms
81:	learn: 0.4016030	total: 221ms	remaining: 202ms
82:	learn: 0.4015753	total: 223ms	remaining: 199ms
83:	learn: 0.4015437	total: 226ms	remaining: 196ms
84:	learn: 0.4014842	total: 228ms	remaining: 193ms
85:	learn: 0.4014554	total: 230ms	remaining: 190ms
86:	learn: 0.4014097	total: 233ms	remaining: 187ms
87:	learn: 0.4013526	total: 235ms	remaining: 184ms
88:	learn: 0.4012662	total: 238ms	remaining: 182ms
89:	learn: 0.4012400	total: 240ms	remaining: 179ms
90:	learn: 0.4012249	total: 242ms	remaining: 176ms
91:	learn: 0.4011865	total: 245ms	remaining: 173ms
92:	learn: 0.4011422	total: 248

140:	learn: 0.3996991	total: 363ms	remaining: 41.1ms
141:	learn: 0.3996759	total: 365ms	remaining: 38.6ms
142:	learn: 0.3996340	total: 368ms	remaining: 36ms
143:	learn: 0.3995957	total: 371ms	remaining: 33.5ms
144:	learn: 0.3995699	total: 374ms	remaining: 31ms
145:	learn: 0.3995449	total: 377ms	remaining: 28.4ms
146:	learn: 0.3994869	total: 380ms	remaining: 25.8ms
147:	learn: 0.3994571	total: 382ms	remaining: 23.2ms
148:	learn: 0.3994291	total: 385ms	remaining: 20.7ms
149:	learn: 0.3993978	total: 387ms	remaining: 18.1ms
150:	learn: 0.3993568	total: 390ms	remaining: 15.5ms
151:	learn: 0.3993264	total: 392ms	remaining: 12.9ms
152:	learn: 0.3992851	total: 395ms	remaining: 10.3ms
153:	learn: 0.3992556	total: 398ms	remaining: 7.74ms
154:	learn: 0.3992132	total: 400ms	remaining: 5.16ms
155:	learn: 0.3991975	total: 402ms	remaining: 2.58ms
156:	learn: 0.3991710	total: 405ms	remaining: 0us
0:	learn: 0.6494142	total: 3.64ms	remaining: 568ms
1:	learn: 0.6137822	total: 6.71ms	remaining: 520ms
2:	l

152:	learn: 0.4023527	total: 393ms	remaining: 10.3ms
153:	learn: 0.4023077	total: 395ms	remaining: 7.7ms
154:	learn: 0.4022737	total: 398ms	remaining: 5.13ms
155:	learn: 0.4022357	total: 401ms	remaining: 2.57ms
156:	learn: 0.4021956	total: 403ms	remaining: 0us
0:	learn: 0.6490520	total: 3.31ms	remaining: 516ms
1:	learn: 0.6131220	total: 6.24ms	remaining: 484ms
2:	learn: 0.5827837	total: 8.82ms	remaining: 453ms
3:	learn: 0.5578824	total: 11.4ms	remaining: 438ms
4:	learn: 0.5366117	total: 14.1ms	remaining: 429ms
5:	learn: 0.5192453	total: 16.9ms	remaining: 424ms
6:	learn: 0.5037946	total: 19.5ms	remaining: 418ms
7:	learn: 0.4909550	total: 22ms	remaining: 410ms
8:	learn: 0.4794287	total: 25.4ms	remaining: 417ms
9:	learn: 0.4699778	total: 28.1ms	remaining: 413ms
10:	learn: 0.4613880	total: 31ms	remaining: 412ms
11:	learn: 0.4545570	total: 33.9ms	remaining: 409ms
12:	learn: 0.4487075	total: 36.7ms	remaining: 407ms
13:	learn: 0.4436994	total: 39.4ms	remaining: 403ms
14:	learn: 0.4390221	tota

0:	learn: 0.6491593	total: 3.56ms	remaining: 555ms
1:	learn: 0.6129849	total: 7.03ms	remaining: 545ms
2:	learn: 0.5824683	total: 9.56ms	remaining: 491ms
3:	learn: 0.5573919	total: 12.2ms	remaining: 466ms
4:	learn: 0.5359689	total: 14.9ms	remaining: 452ms
5:	learn: 0.5185750	total: 17.9ms	remaining: 451ms
6:	learn: 0.5030374	total: 20.6ms	remaining: 442ms
7:	learn: 0.4901561	total: 23.3ms	remaining: 433ms
8:	learn: 0.4785717	total: 25.9ms	remaining: 426ms
9:	learn: 0.4689968	total: 28.4ms	remaining: 418ms
10:	learn: 0.4603929	total: 31.1ms	remaining: 413ms
11:	learn: 0.4534230	total: 33.6ms	remaining: 406ms
12:	learn: 0.4470251	total: 36.3ms	remaining: 402ms
13:	learn: 0.4419375	total: 39ms	remaining: 398ms
14:	learn: 0.4373062	total: 41.8ms	remaining: 395ms
15:	learn: 0.4332042	total: 44.2ms	remaining: 390ms
16:	learn: 0.4293008	total: 46.9ms	remaining: 386ms
17:	learn: 0.4263705	total: 49.5ms	remaining: 383ms
18:	learn: 0.4241756	total: 52.2ms	remaining: 379ms
19:	learn: 0.4220347	tot

70:	learn: 0.4022252	total: 184ms	remaining: 223ms
71:	learn: 0.4021484	total: 187ms	remaining: 221ms
72:	learn: 0.4021046	total: 190ms	remaining: 218ms
73:	learn: 0.4020365	total: 192ms	remaining: 216ms
74:	learn: 0.4019972	total: 195ms	remaining: 213ms
75:	learn: 0.4019339	total: 198ms	remaining: 211ms
76:	learn: 0.4019071	total: 201ms	remaining: 209ms
77:	learn: 0.4018617	total: 204ms	remaining: 207ms
78:	learn: 0.4017712	total: 207ms	remaining: 204ms
79:	learn: 0.4017186	total: 209ms	remaining: 201ms
80:	learn: 0.4016711	total: 212ms	remaining: 199ms
81:	learn: 0.4016030	total: 215ms	remaining: 196ms
82:	learn: 0.4015753	total: 217ms	remaining: 194ms
83:	learn: 0.4015437	total: 220ms	remaining: 191ms
84:	learn: 0.4014842	total: 222ms	remaining: 188ms
85:	learn: 0.4014554	total: 224ms	remaining: 185ms
86:	learn: 0.4014097	total: 227ms	remaining: 182ms
87:	learn: 0.4013526	total: 229ms	remaining: 180ms
88:	learn: 0.4012662	total: 232ms	remaining: 177ms
89:	learn: 0.4012400	total: 234

142:	learn: 0.3996340	total: 363ms	remaining: 35.6ms
143:	learn: 0.3995957	total: 366ms	remaining: 33.1ms
144:	learn: 0.3995699	total: 369ms	remaining: 30.5ms
145:	learn: 0.3995449	total: 372ms	remaining: 28ms
146:	learn: 0.3994869	total: 374ms	remaining: 25.5ms
147:	learn: 0.3994571	total: 377ms	remaining: 22.9ms
148:	learn: 0.3994291	total: 380ms	remaining: 20.4ms
149:	learn: 0.3993978	total: 382ms	remaining: 17.8ms
150:	learn: 0.3993568	total: 385ms	remaining: 15.3ms
151:	learn: 0.3993264	total: 387ms	remaining: 12.7ms
152:	learn: 0.3992851	total: 390ms	remaining: 10.2ms
153:	learn: 0.3992556	total: 393ms	remaining: 7.65ms
154:	learn: 0.3992132	total: 395ms	remaining: 5.1ms
155:	learn: 0.3991975	total: 397ms	remaining: 2.55ms
156:	learn: 0.3991710	total: 400ms	remaining: 0us
0:	learn: 0.6494142	total: 14.3ms	remaining: 2.23s
1:	learn: 0.6137822	total: 17.4ms	remaining: 1.35s
2:	learn: 0.5837473	total: 20.2ms	remaining: 1.03s
3:	learn: 0.5590740	total: 22.8ms	remaining: 870ms
4:	lear

149:	learn: 0.4024764	total: 393ms	remaining: 18.3ms
150:	learn: 0.4024442	total: 396ms	remaining: 15.7ms
151:	learn: 0.4023680	total: 398ms	remaining: 13.1ms
152:	learn: 0.4023527	total: 401ms	remaining: 10.5ms
153:	learn: 0.4023077	total: 404ms	remaining: 7.87ms
154:	learn: 0.4022737	total: 407ms	remaining: 5.25ms
155:	learn: 0.4022357	total: 409ms	remaining: 2.62ms
156:	learn: 0.4021956	total: 412ms	remaining: 0us
0:	learn: 0.6490520	total: 3.54ms	remaining: 553ms
1:	learn: 0.6131220	total: 6.71ms	remaining: 520ms
2:	learn: 0.5827837	total: 9.72ms	remaining: 499ms
3:	learn: 0.5578824	total: 12.6ms	remaining: 481ms
4:	learn: 0.5366117	total: 15.6ms	remaining: 475ms
5:	learn: 0.5192453	total: 18.7ms	remaining: 470ms
6:	learn: 0.5037946	total: 21.2ms	remaining: 455ms
7:	learn: 0.4909550	total: 24.1ms	remaining: 448ms
8:	learn: 0.4794287	total: 26.7ms	remaining: 439ms
9:	learn: 0.4699778	total: 29.5ms	remaining: 433ms
10:	learn: 0.4613880	total: 31.9ms	remaining: 424ms
11:	learn: 0.4545

In [35]:
pd.DataFrame(model_scores).round(4)

Model Name  Accuracy train  \
0                                  LogisticRegression        0.819900   
1                              DecisionTreeClassifier        0.832200   
2                              RandomForestClassifier        0.833100   
3                                          GaussianNB        0.791100   
4                                         BernoulliNB        0.819500   
5                                  AdaBoostClassifier        0.829400   
6                          GradientBoostingClassifier        0.831200   
7                                       XGBClassifier        0.833100   
8   <catboost.core.CatBoostClassifier object at 0x...        0.832700   
9                                      LGBMClassifier        0.834700   
10                               KNeighborsClassifier        0.850200   

    Precision train  Recall train  F1 train  F1 Avg Weighted train  \
0          0.758000      0.158800  0.262600               0.769200   
1          0.767700      0.242600  0.368700               0.795300   
2          0.773700      0.245500  0.372700               0.796500   
3          0.472400      0.292600  0.361400               0.771400   
4          0.685800      0.195700  0.304600               0.776800   
5          0.730700      0.245500  0.367600               0.793600   
6          0.763000      0.238000  0.362800               0.793700   
7          0.761000      0.252900  0.379600               0.797800   
8          0.767200      0.246100  0.372700               0.796300   
9          0.781700      0.251600  0.380700               0.798800   
10         0.737300      0.401400  0.519800               0.832200   

    ROC AUC train  Accuracy test  Precision test  Recall test  F1 test  \
0        0.740900       0.818300        0.750200     0.150200 0.250300   
1        0.790500       0.828000        0.741400     0.227700 0.348500   
2        0.797000       0.829000        0.750900     0.229500 0.351600   
3        0.697800       0.789500        0.465800     0.289300 0.356900   
4        0.713700       0.817200        0.671900     0.185600 0.290900   
5        0.771900       0.826300        0.716300     0.231500 0.349900   
6        0.775300       0.828900        0.753500     0.226900 0.348700   
7        0.791800       0.828200        0.733600     0.234500 0.355400   
8        0.789100       0.829200        0.749200     0.231500 0.353700   
9        0.802000       0.829400        0.751900     0.231300 0.353800   
10       0.870100       0.803600        0.526500     0.274900 0.361200   

    F1 Avg Weighted test  ROC AUC test  CV-5-Mean  CV-5-SD  
0               0.766100      0.739800   0.769200 0.003100  
1               0.789400      0.777000   0.791700 0.004300  
2               0.790500      0.782400   0.794100 0.005200  
3               0.769700      0.696500   0.770800 0.003200  
4               0.773100      0.712800   0.776700 0.004500  
5               0.788700      0.769000   0.793200 0.005400  
6               0.789900      0.773900   0.794200 0.004700  
7               0.790700      0.778900   0.794400 0.004800  
8               0.790900      0.783600   0.795500 0.005500  
9               0.791100      0.782600   0.794500 0.004800  
10              0.778400      0.687200   0.776000 0.004000

In [36]:
from imblearn.over_sampling import SMOTE
from collections import Counter

counter = Counter(y_train)
print('Before', counter)

smt = SMOTE(random_state=10)
X_train_sm, y_train_sm = smt.fit_resample(X_train, y_train)

counter = Counter(y_train_sm)
print('After', counter)

Before Counter({0: 61743, 1: 15623})
After Counter({0: 61743, 1: 61743})


In [37]:
lr_pipeline = Pipeline([
    ('lr_model', LogisticRegression(**rsearch_lr.best_params_))
])

In [38]:
dt_pipeline = Pipeline([
    ('dt_model', DecisionTreeClassifier(**rsearch_dt.best_params_,random_state=42))
])

In [39]:
rf_pipeline = Pipeline([
    ('rf_model', RandomForestClassifier(**rsearch_rf.best_params_,random_state=42))
])

In [40]:
gnb_pipeline = Pipeline([
    ('gnb_model', GaussianNB())
])

In [41]:
bnb_pipeline = Pipeline([
    ('bnb_model', BernoulliNB())
])

In [42]:
knn_pipeline = Pipeline([
    ('knn_model', KNeighborsClassifier())
])

In [43]:
ada_pipeline = Pipeline([
    ('rf_model', AdaBoostClassifier(**rsearch_ada.best_params_, random_state = 42))
])

In [44]:
gb_pipeline = Pipeline([
    ('rf_model', GradientBoostingClassifier(**rsearch_gb.best_params_, random_state = 42))
])

In [45]:
cb_pipeline = Pipeline([
    ('cb_model', CatBoostClassifier(**rsearch_cb.best_params_, random_state = 42))
])

In [46]:
lgbm_pipeline = Pipeline([
    ('lgbm_model', LGBMClassifier(**rsearch_lgbm.best_params_, random_state = 42))
])

In [47]:
xgb_pipeline = Pipeline([
    ('rf_model', XGBClassifier(**rsearch_xgb.best_params_, random_state = 42))
])

In [48]:
pipe_all = [lr_pipeline, dt_pipeline, rf_pipeline, gnb_pipeline, bnb_pipeline, ada_pipeline, gb_pipeline, xgb_pipeline, cb_pipeline, lgbm_pipeline,
            knn_pipeline]
            
for pipe in pipe_all:
  pipe.fit(X_train_sm, y_train_sm)

0:	learn: 0.6692326	total: 12.2ms	remaining: 1.9s
1:	learn: 0.6490189	total: 17.1ms	remaining: 1.32s
2:	learn: 0.6320210	total: 21.5ms	remaining: 1.1s
3:	learn: 0.6177178	total: 25.9ms	remaining: 990ms
4:	learn: 0.6058867	total: 30ms	remaining: 911ms
5:	learn: 0.5955977	total: 34.2ms	remaining: 862ms
6:	learn: 0.5869244	total: 38.5ms	remaining: 826ms
7:	learn: 0.5792919	total: 42.8ms	remaining: 798ms
8:	learn: 0.5720861	total: 47.1ms	remaining: 774ms
9:	learn: 0.5664071	total: 51.1ms	remaining: 751ms
10:	learn: 0.5615471	total: 55.3ms	remaining: 734ms
11:	learn: 0.5574987	total: 59.4ms	remaining: 718ms
12:	learn: 0.5529654	total: 63.6ms	remaining: 705ms
13:	learn: 0.5495753	total: 68.1ms	remaining: 696ms
14:	learn: 0.5464389	total: 72.6ms	remaining: 688ms
15:	learn: 0.5428501	total: 77.2ms	remaining: 680ms
16:	learn: 0.5406676	total: 81.4ms	remaining: 671ms
17:	learn: 0.5385484	total: 85.9ms	remaining: 663ms
18:	learn: 0.5358866	total: 90.8ms	remaining: 660ms
19:	learn: 0.5332505	total

In [49]:
for model in pipe_all:
    
    model_scores['Model Name'].append(str(model[0]).split('(')[0] + " SMOTE")
    
    model_scores['Accuracy train'].append(model.score(X_train_sm, y_train_sm))
    pred_tr = model.predict(X_train_sm)
    prob_tr = model.predict_proba(X_train_sm)[:,1]
    model_scores['Precision train'].append(precision_score(y_train_sm, pred_tr))
    model_scores['Recall train'].append(recall_score(y_train_sm, pred_tr))
    model_scores['F1 train'].append(f1_score(y_train_sm, pred_tr))
    model_scores['F1 Avg Weighted train'].append(f1_score(y_train_sm, pred_tr, average = 'weighted'))
    model_scores['ROC AUC train'].append(roc_auc_score(y_train_sm, prob_tr))
    
    model_scores['Accuracy test'].append(model.score(X_test, y_test))
    pred_ts = model.predict(X_test)
    prob_ts = model.predict_proba(X_test)[:,1]
    model_scores['Precision test'].append(precision_score(y_test, pred_ts))
    model_scores['Recall test'].append(recall_score(y_test, pred_ts))
    model_scores['F1 test'].append(f1_score(y_test, pred_ts))
    model_scores['F1 Avg Weighted test'].append(f1_score(y_test, pred_ts, average = 'weighted'))
    model_scores['ROC AUC test'].append(roc_auc_score(y_test, prob_ts))

    model_scores['CV-5-Mean'].append(cross_val_score(model,X_train_sm,y_train_sm,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').mean())
    model_scores['CV-5-SD'].append(cross_val_score(model,X_train_sm,y_train_sm,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').std())

0:	learn: 0.6687819	total: 17.7ms	remaining: 2.76s
1:	learn: 0.6485433	total: 22.1ms	remaining: 1.71s
2:	learn: 0.6322529	total: 25.6ms	remaining: 1.31s
3:	learn: 0.6181383	total: 29.3ms	remaining: 1.12s
4:	learn: 0.6062821	total: 33ms	remaining: 1s
5:	learn: 0.5961008	total: 36.8ms	remaining: 925ms
6:	learn: 0.5871661	total: 40.3ms	remaining: 863ms
7:	learn: 0.5795836	total: 44.1ms	remaining: 821ms
8:	learn: 0.5729027	total: 47.8ms	remaining: 785ms
9:	learn: 0.5671494	total: 51.3ms	remaining: 754ms
10:	learn: 0.5614220	total: 55ms	remaining: 730ms
11:	learn: 0.5562296	total: 58.9ms	remaining: 712ms
12:	learn: 0.5521945	total: 62.5ms	remaining: 692ms
13:	learn: 0.5486287	total: 66.1ms	remaining: 675ms
14:	learn: 0.5458545	total: 69.8ms	remaining: 661ms
15:	learn: 0.5431341	total: 73.4ms	remaining: 647ms
16:	learn: 0.5409094	total: 77.2ms	remaining: 636ms
17:	learn: 0.5386006	total: 81.1ms	remaining: 626ms
18:	learn: 0.5357528	total: 85.1ms	remaining: 618ms
19:	learn: 0.5328770	total: 8

46:	learn: 0.5024131	total: 195ms	remaining: 456ms
47:	learn: 0.5011591	total: 198ms	remaining: 451ms
48:	learn: 0.5006257	total: 202ms	remaining: 446ms
49:	learn: 0.5002077	total: 206ms	remaining: 441ms
50:	learn: 0.4997415	total: 209ms	remaining: 435ms
51:	learn: 0.4988910	total: 213ms	remaining: 431ms
52:	learn: 0.4984505	total: 217ms	remaining: 426ms
53:	learn: 0.4977565	total: 220ms	remaining: 420ms
54:	learn: 0.4972989	total: 224ms	remaining: 415ms
55:	learn: 0.4968986	total: 227ms	remaining: 410ms
56:	learn: 0.4961398	total: 231ms	remaining: 406ms
57:	learn: 0.4952447	total: 235ms	remaining: 401ms
58:	learn: 0.4947890	total: 238ms	remaining: 396ms
59:	learn: 0.4944429	total: 242ms	remaining: 391ms
60:	learn: 0.4939221	total: 245ms	remaining: 386ms
61:	learn: 0.4936080	total: 248ms	remaining: 381ms
62:	learn: 0.4932156	total: 252ms	remaining: 376ms
63:	learn: 0.4928022	total: 255ms	remaining: 371ms
64:	learn: 0.4921645	total: 259ms	remaining: 367ms
65:	learn: 0.4915796	total: 263

50:	learn: 0.4992561	total: 212ms	remaining: 440ms
51:	learn: 0.4986677	total: 216ms	remaining: 435ms
52:	learn: 0.4981908	total: 219ms	remaining: 431ms
53:	learn: 0.4976010	total: 224ms	remaining: 426ms
54:	learn: 0.4968563	total: 227ms	remaining: 421ms
55:	learn: 0.4965916	total: 231ms	remaining: 416ms
56:	learn: 0.4959081	total: 234ms	remaining: 411ms
57:	learn: 0.4954700	total: 238ms	remaining: 406ms
58:	learn: 0.4951015	total: 241ms	remaining: 400ms
59:	learn: 0.4947981	total: 244ms	remaining: 395ms
60:	learn: 0.4941591	total: 248ms	remaining: 390ms
61:	learn: 0.4930627	total: 252ms	remaining: 386ms
62:	learn: 0.4926858	total: 255ms	remaining: 381ms
63:	learn: 0.4921073	total: 259ms	remaining: 376ms
64:	learn: 0.4915112	total: 263ms	remaining: 372ms
65:	learn: 0.4909226	total: 266ms	remaining: 367ms
66:	learn: 0.4894659	total: 270ms	remaining: 362ms
67:	learn: 0.4891732	total: 273ms	remaining: 358ms
68:	learn: 0.4887176	total: 277ms	remaining: 353ms
69:	learn: 0.4885092	total: 280

105:	learn: 0.4718333	total: 392ms	remaining: 188ms
106:	learn: 0.4714792	total: 395ms	remaining: 185ms
107:	learn: 0.4707556	total: 399ms	remaining: 181ms
108:	learn: 0.4702212	total: 403ms	remaining: 178ms
109:	learn: 0.4698706	total: 407ms	remaining: 174ms
110:	learn: 0.4696787	total: 411ms	remaining: 170ms
111:	learn: 0.4691286	total: 414ms	remaining: 166ms
112:	learn: 0.4687461	total: 418ms	remaining: 163ms
113:	learn: 0.4677063	total: 421ms	remaining: 159ms
114:	learn: 0.4670966	total: 425ms	remaining: 155ms
115:	learn: 0.4656812	total: 429ms	remaining: 152ms
116:	learn: 0.4644135	total: 433ms	remaining: 148ms
117:	learn: 0.4631781	total: 437ms	remaining: 144ms
118:	learn: 0.4628662	total: 440ms	remaining: 140ms
119:	learn: 0.4622930	total: 443ms	remaining: 137ms
120:	learn: 0.4621201	total: 447ms	remaining: 133ms
121:	learn: 0.4614534	total: 450ms	remaining: 129ms
122:	learn: 0.4611774	total: 453ms	remaining: 125ms
123:	learn: 0.4599308	total: 457ms	remaining: 122ms
124:	learn: 

154:	learn: 0.4422375	total: 577ms	remaining: 7.44ms
155:	learn: 0.4412473	total: 581ms	remaining: 3.73ms
156:	learn: 0.4410472	total: 585ms	remaining: 0us
0:	learn: 0.6687819	total: 13.5ms	remaining: 2.11s
1:	learn: 0.6485433	total: 18.5ms	remaining: 1.43s
2:	learn: 0.6322529	total: 22.8ms	remaining: 1.17s
3:	learn: 0.6181383	total: 26.9ms	remaining: 1.03s
4:	learn: 0.6062821	total: 30.7ms	remaining: 935ms
5:	learn: 0.5961008	total: 34.5ms	remaining: 869ms
6:	learn: 0.5871661	total: 38ms	remaining: 815ms
7:	learn: 0.5795836	total: 41.6ms	remaining: 775ms
8:	learn: 0.5729027	total: 45.2ms	remaining: 744ms
9:	learn: 0.5671494	total: 48.7ms	remaining: 716ms
10:	learn: 0.5614220	total: 52.3ms	remaining: 695ms
11:	learn: 0.5562296	total: 56.3ms	remaining: 681ms
12:	learn: 0.5521945	total: 59.9ms	remaining: 664ms
13:	learn: 0.5486287	total: 63.5ms	remaining: 649ms
14:	learn: 0.5458545	total: 67.3ms	remaining: 637ms
15:	learn: 0.5431341	total: 70.9ms	remaining: 625ms
16:	learn: 0.5409094	tot

0:	learn: 0.6688236	total: 18.3ms	remaining: 2.85s
1:	learn: 0.6485957	total: 22.7ms	remaining: 1.76s
2:	learn: 0.6320758	total: 26.4ms	remaining: 1.36s
3:	learn: 0.6180874	total: 30ms	remaining: 1.15s
4:	learn: 0.6065879	total: 33.6ms	remaining: 1.02s
5:	learn: 0.5962825	total: 37.3ms	remaining: 939ms
6:	learn: 0.5879315	total: 40.8ms	remaining: 875ms
7:	learn: 0.5805335	total: 44.4ms	remaining: 827ms
8:	learn: 0.5742492	total: 48.1ms	remaining: 791ms
9:	learn: 0.5684478	total: 51.6ms	remaining: 758ms
10:	learn: 0.5634406	total: 55.2ms	remaining: 733ms
11:	learn: 0.5581628	total: 59ms	remaining: 713ms
12:	learn: 0.5535474	total: 62.6ms	remaining: 693ms
13:	learn: 0.5500466	total: 66.1ms	remaining: 675ms
14:	learn: 0.5464956	total: 69.8ms	remaining: 661ms
15:	learn: 0.5436705	total: 73.5ms	remaining: 647ms
16:	learn: 0.5413989	total: 77.7ms	remaining: 640ms
17:	learn: 0.5390389	total: 81.4ms	remaining: 628ms
18:	learn: 0.5370747	total: 85ms	remaining: 618ms
19:	learn: 0.5350318	total: 

49:	learn: 0.5002963	total: 220ms	remaining: 470ms
50:	learn: 0.4992561	total: 224ms	remaining: 465ms
51:	learn: 0.4986677	total: 228ms	remaining: 460ms
52:	learn: 0.4981908	total: 232ms	remaining: 455ms
53:	learn: 0.4976010	total: 236ms	remaining: 449ms
54:	learn: 0.4968563	total: 239ms	remaining: 444ms
55:	learn: 0.4965916	total: 243ms	remaining: 438ms
56:	learn: 0.4959081	total: 247ms	remaining: 433ms
57:	learn: 0.4954700	total: 250ms	remaining: 427ms
58:	learn: 0.4951015	total: 254ms	remaining: 422ms
59:	learn: 0.4947981	total: 257ms	remaining: 416ms
60:	learn: 0.4941591	total: 261ms	remaining: 411ms
61:	learn: 0.4930627	total: 265ms	remaining: 406ms
62:	learn: 0.4926858	total: 269ms	remaining: 401ms
63:	learn: 0.4921073	total: 272ms	remaining: 396ms
64:	learn: 0.4915112	total: 276ms	remaining: 391ms
65:	learn: 0.4909226	total: 279ms	remaining: 385ms
66:	learn: 0.4894659	total: 283ms	remaining: 380ms
67:	learn: 0.4891732	total: 286ms	remaining: 375ms
68:	learn: 0.4887176	total: 290

102:	learn: 0.4728356	total: 385ms	remaining: 202ms
103:	learn: 0.4726321	total: 389ms	remaining: 198ms
104:	learn: 0.4720376	total: 393ms	remaining: 194ms
105:	learn: 0.4718333	total: 397ms	remaining: 191ms
106:	learn: 0.4714792	total: 401ms	remaining: 187ms
107:	learn: 0.4707556	total: 404ms	remaining: 183ms
108:	learn: 0.4702212	total: 408ms	remaining: 180ms
109:	learn: 0.4698706	total: 412ms	remaining: 176ms
110:	learn: 0.4696787	total: 416ms	remaining: 172ms
111:	learn: 0.4691286	total: 419ms	remaining: 168ms
112:	learn: 0.4687461	total: 423ms	remaining: 165ms
113:	learn: 0.4677063	total: 426ms	remaining: 161ms
114:	learn: 0.4670966	total: 430ms	remaining: 157ms
115:	learn: 0.4656812	total: 434ms	remaining: 153ms
116:	learn: 0.4644135	total: 438ms	remaining: 150ms
117:	learn: 0.4631781	total: 441ms	remaining: 146ms
118:	learn: 0.4628662	total: 445ms	remaining: 142ms
119:	learn: 0.4622930	total: 448ms	remaining: 138ms
120:	learn: 0.4621201	total: 451ms	remaining: 134ms
121:	learn: 

149:	learn: 0.4451388	total: 542ms	remaining: 25.3ms
150:	learn: 0.4449239	total: 546ms	remaining: 21.7ms
151:	learn: 0.4437178	total: 550ms	remaining: 18.1ms
152:	learn: 0.4432934	total: 555ms	remaining: 14.5ms
153:	learn: 0.4427062	total: 558ms	remaining: 10.9ms
154:	learn: 0.4422375	total: 562ms	remaining: 7.25ms
155:	learn: 0.4412473	total: 566ms	remaining: 3.63ms
156:	learn: 0.4410472	total: 570ms	remaining: 0us


In [50]:
pd.DataFrame(model_scores).round(4)

Model Name  Accuracy train  \
0                                  LogisticRegression        0.819900   
1                              DecisionTreeClassifier        0.832200   
2                              RandomForestClassifier        0.833100   
3                                          GaussianNB        0.791100   
4                                         BernoulliNB        0.819500   
5                                  AdaBoostClassifier        0.829400   
6                          GradientBoostingClassifier        0.831200   
7                                       XGBClassifier        0.833100   
8   <catboost.core.CatBoostClassifier object at 0x...        0.832700   
9                                      LGBMClassifier        0.834700   
10                               KNeighborsClassifier        0.850200   
11                           LogisticRegression SMOTE        0.674800   
12                       DecisionTreeClassifier SMOTE        0.736500   
13                       RandomForestClassifier SMOTE        0.749700   
14                                   GaussianNB SMOTE        0.649400   
15                                  BernoulliNB SMOTE        0.666600   
16                           AdaBoostClassifier SMOTE        0.734100   
17                   GradientBoostingClassifier SMOTE        0.731800   
18                                XGBClassifier SMOTE        0.875500   
19  <catboost.core.CatBoostClassifier object at 0x...        0.799200   
20                               LGBMClassifier SMOTE        0.824100   
21                         KNeighborsClassifier SMOTE        0.846600   

    Precision train  Recall train  F1 train  F1 Avg Weighted train  \
0          0.758000      0.158800  0.262600               0.769200   
1          0.767700      0.242600  0.368700               0.795300   
2          0.773700      0.245500  0.372700               0.796500   
3          0.472400      0.292600  0.361400               0.771400   
4          0.685800      0.195700  0.304600               0.776800   
5          0.730700      0.245500  0.367600               0.793600   
6          0.763000      0.238000  0.362800               0.793700   
7          0.761000      0.252900  0.379600               0.797800   
8          0.767200      0.246100  0.372700               0.796300   
9          0.781700      0.251600  0.380700               0.798800   
10         0.737300      0.401400  0.519800               0.832200   
11         0.703300      0.604800  0.650300               0.673200   
12         0.739800      0.729500  0.734600               0.736500   
13         0.726000      0.802100  0.762200               0.749000   
14         0.641200      0.678500  0.659300               0.649100   
15         0.683900      0.619400  0.650100               0.665800   
16         0.710900      0.789000  0.747900               0.733300   
17         0.699100      0.814000  0.752200               0.730000   
18         0.956400      0.786800  0.863400               0.874500   
19         0.803700      0.791800  0.797700               0.799200   
20         0.841000      0.799200  0.819600               0.824000   
21         0.823100      0.883000  0.852000               0.846400   

    ROC AUC train  Accuracy test  Precision test  Recall test  F1 test  \
0        0.740900       0.818300        0.750200     0.150200 0.250300   
1        0.790500       0.828000        0.741400     0.227700 0.348500   
2        0.797000       0.829000        0.750900     0.229500 0.351600   
3        0.697800       0.789500        0.465800     0.289300 0.356900   
4        0.713700       0.817200        0.671900     0.185600 0.290900   
5        0.771900       0.826300        0.716300     0.231500 0.349900   
6        0.775300       0.828900        0.753500     0.226900 0.348700   
7        0.791800       0.828200        0.733600     0.234500 0.355400   
8        0.789100       0.829200        0.749200     0.231500 0.353700   
9        0.8

In [51]:
from imblearn.over_sampling import ADASYN
from collections import Counter

counter = Counter(y_train)
print('Before', counter)

ada = ADASYN(random_state=10)
X_train_as, y_train_as = ada.fit_resample(X_train, y_train)

counter = Counter(y_train_as)
print('After', counter)

Before Counter({0: 61743, 1: 15623})
After Counter({1: 64826, 0: 61743})


In [52]:
lr_pipeline = Pipeline([
    ('lr_model', LogisticRegression(**rsearch_lr.best_params_))
])

In [53]:
dt_pipeline = Pipeline([
    ('dt_model', DecisionTreeClassifier(**rsearch_dt.best_params_,random_state=42))
])

In [54]:
rf_pipeline = Pipeline([
    ('rf_model', RandomForestClassifier(**rsearch_rf.best_params_,random_state=42))
])

In [55]:
gnb_pipeline = Pipeline([
    ('gnb_model', GaussianNB())
])

In [56]:
bnb_pipeline = Pipeline([
    ('bnb_model', BernoulliNB())
])

In [57]:
knn_pipeline = Pipeline([
    ('knn_model', KNeighborsClassifier())
])

In [58]:
ada_pipeline = Pipeline([
    ('rf_model', AdaBoostClassifier(**rsearch_ada.best_params_, random_state = 42))
])

In [59]:
gb_pipeline = Pipeline([
    ('rf_model', GradientBoostingClassifier(**rsearch_gb.best_params_, random_state = 42))
])

In [60]:
cb_pipeline = Pipeline([
    ('cb_model', CatBoostClassifier(**rsearch_cb.best_params_, random_state = 42))
])

In [61]:
lgbm_pipeline = Pipeline([
    ('lgbm_model', LGBMClassifier(**rsearch_lgbm.best_params_, random_state = 42))
])

In [62]:
xgb_pipeline = Pipeline([
    ('rf_model', XGBClassifier(**rsearch_xgb.best_params_, random_state = 42))
])

In [63]:
pipe_all = [lr_pipeline, dt_pipeline, rf_pipeline, gnb_pipeline, bnb_pipeline, ada_pipeline, gb_pipeline, xgb_pipeline, cb_pipeline, lgbm_pipeline,
            knn_pipeline]
            
for pipe in pipe_all:
  pipe.fit(X_train_as, y_train_as)

0:	learn: 0.6724519	total: 30.5ms	remaining: 4.75s
1:	learn: 0.6557888	total: 36.8ms	remaining: 2.85s
2:	learn: 0.6415076	total: 42.5ms	remaining: 2.18s
3:	learn: 0.6296913	total: 47.9ms	remaining: 1.83s
4:	learn: 0.6200406	total: 53.7ms	remaining: 1.63s
5:	learn: 0.6115228	total: 59.6ms	remaining: 1.5s
6:	learn: 0.6040455	total: 64.7ms	remaining: 1.39s
7:	learn: 0.5979419	total: 70.2ms	remaining: 1.31s
8:	learn: 0.5928693	total: 75.2ms	remaining: 1.24s
9:	learn: 0.5877041	total: 81.1ms	remaining: 1.19s
10:	learn: 0.5837753	total: 85.8ms	remaining: 1.14s
11:	learn: 0.5800546	total: 91.2ms	remaining: 1.1s
12:	learn: 0.5770377	total: 97.2ms	remaining: 1.08s
13:	learn: 0.5736358	total: 102ms	remaining: 1.05s
14:	learn: 0.5709415	total: 108ms	remaining: 1.02s
15:	learn: 0.5687667	total: 114ms	remaining: 1s
16:	learn: 0.5654793	total: 120ms	remaining: 989ms
17:	learn: 0.5629136	total: 126ms	remaining: 970ms
18:	learn: 0.5603839	total: 132ms	remaining: 957ms
19:	learn: 0.5590175	total: 137ms

In [64]:
for model in pipe_all:
    
    model_scores['Model Name'].append(str(model[0]).split('(')[0] + " ADASYN")
    
    model_scores['Accuracy train'].append(model.score(X_train_as, y_train_as))
    pred_tr = model.predict(X_train_as)
    prob_tr = model.predict_proba(X_train_as)[:,1]
    model_scores['Precision train'].append(precision_score(y_train_as, pred_tr))
    model_scores['Recall train'].append(recall_score(y_train_as, pred_tr))
    model_scores['F1 train'].append(f1_score(y_train_as, pred_tr))
    model_scores['F1 Avg Weighted train'].append(f1_score(y_train_as, pred_tr, average = 'weighted'))
    model_scores['ROC AUC train'].append(roc_auc_score(y_train_as, prob_tr))
    
    model_scores['Accuracy test'].append(model.score(X_test, y_test))
    pred_ts = model.predict(X_test)
    prob_ts = model.predict_proba(X_test)[:,1]
    model_scores['Precision test'].append(precision_score(y_test, pred_ts))
    model_scores['Recall test'].append(recall_score(y_test, pred_ts))
    model_scores['F1 test'].append(f1_score(y_test, pred_ts))
    model_scores['F1 Avg Weighted test'].append(f1_score(y_test, pred_ts, average = 'weighted'))
    model_scores['ROC AUC test'].append(roc_auc_score(y_test, prob_ts))

    model_scores['CV-5-Mean'].append(cross_val_score(model,X_train_as,y_train_as,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').mean())
    model_scores['CV-5-SD'].append(cross_val_score(model,X_train_as,y_train_as,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').std())

0:	learn: 0.6723705	total: 36ms	remaining: 5.61s
1:	learn: 0.6553111	total: 40.6ms	remaining: 3.15s
2:	learn: 0.6415267	total: 44.3ms	remaining: 2.27s
3:	learn: 0.6291752	total: 48ms	remaining: 1.83s
4:	learn: 0.6194436	total: 51.6ms	remaining: 1.57s
5:	learn: 0.6108060	total: 55.2ms	remaining: 1.39s
6:	learn: 0.6037534	total: 58.9ms	remaining: 1.26s
7:	learn: 0.5975739	total: 62.4ms	remaining: 1.16s
8:	learn: 0.5914398	total: 66.1ms	remaining: 1.09s
9:	learn: 0.5864645	total: 69.6ms	remaining: 1.02s
10:	learn: 0.5825164	total: 73.3ms	remaining: 973ms
11:	learn: 0.5789578	total: 76.9ms	remaining: 930ms
12:	learn: 0.5760816	total: 80.8ms	remaining: 895ms
13:	learn: 0.5717696	total: 84.7ms	remaining: 865ms
14:	learn: 0.5681830	total: 88.7ms	remaining: 840ms
15:	learn: 0.5656414	total: 92.5ms	remaining: 815ms
16:	learn: 0.5637201	total: 96.1ms	remaining: 791ms
17:	learn: 0.5619121	total: 99.8ms	remaining: 771ms
18:	learn: 0.5595311	total: 104ms	remaining: 754ms
19:	learn: 0.5567974	total:

49:	learn: 0.5261915	total: 208ms	remaining: 445ms
50:	learn: 0.5255203	total: 212ms	remaining: 440ms
51:	learn: 0.5251875	total: 215ms	remaining: 434ms
52:	learn: 0.5245939	total: 219ms	remaining: 429ms
53:	learn: 0.5238707	total: 222ms	remaining: 424ms
54:	learn: 0.5233458	total: 226ms	remaining: 418ms
55:	learn: 0.5228937	total: 229ms	remaining: 413ms
56:	learn: 0.5221038	total: 233ms	remaining: 409ms
57:	learn: 0.5218016	total: 236ms	remaining: 404ms
58:	learn: 0.5203226	total: 240ms	remaining: 399ms
59:	learn: 0.5196845	total: 244ms	remaining: 394ms
60:	learn: 0.5192191	total: 247ms	remaining: 389ms
61:	learn: 0.5187431	total: 251ms	remaining: 384ms
62:	learn: 0.5183976	total: 254ms	remaining: 379ms
63:	learn: 0.5177317	total: 258ms	remaining: 374ms
64:	learn: 0.5169628	total: 261ms	remaining: 370ms
65:	learn: 0.5166248	total: 265ms	remaining: 365ms
66:	learn: 0.5156397	total: 269ms	remaining: 361ms
67:	learn: 0.5152578	total: 272ms	remaining: 356ms
68:	learn: 0.5147641	total: 276

96:	learn: 0.4979133	total: 373ms	remaining: 231ms
97:	learn: 0.4977284	total: 377ms	remaining: 227ms
98:	learn: 0.4968263	total: 381ms	remaining: 223ms
99:	learn: 0.4960964	total: 384ms	remaining: 219ms
100:	learn: 0.4957007	total: 388ms	remaining: 215ms
101:	learn: 0.4951505	total: 391ms	remaining: 211ms
102:	learn: 0.4946602	total: 395ms	remaining: 207ms
103:	learn: 0.4939857	total: 399ms	remaining: 203ms
104:	learn: 0.4921971	total: 403ms	remaining: 200ms
105:	learn: 0.4919596	total: 407ms	remaining: 196ms
106:	learn: 0.4915867	total: 410ms	remaining: 192ms
107:	learn: 0.4912577	total: 414ms	remaining: 188ms
108:	learn: 0.4911544	total: 418ms	remaining: 184ms
109:	learn: 0.4906156	total: 421ms	remaining: 180ms
110:	learn: 0.4891863	total: 425ms	remaining: 176ms
111:	learn: 0.4888492	total: 428ms	remaining: 172ms
112:	learn: 0.4878144	total: 432ms	remaining: 168ms
113:	learn: 0.4871355	total: 436ms	remaining: 164ms
114:	learn: 0.4859133	total: 440ms	remaining: 161ms
115:	learn: 0.48

100:	learn: 0.4932441	total: 405ms	remaining: 224ms
101:	learn: 0.4915785	total: 409ms	remaining: 220ms
102:	learn: 0.4900952	total: 413ms	remaining: 216ms
103:	learn: 0.4895506	total: 416ms	remaining: 212ms
104:	learn: 0.4889756	total: 420ms	remaining: 208ms
105:	learn: 0.4883200	total: 424ms	remaining: 204ms
106:	learn: 0.4879334	total: 427ms	remaining: 200ms
107:	learn: 0.4876194	total: 431ms	remaining: 196ms
108:	learn: 0.4871952	total: 434ms	remaining: 191ms
109:	learn: 0.4866931	total: 438ms	remaining: 187ms
110:	learn: 0.4857518	total: 442ms	remaining: 183ms
111:	learn: 0.4852222	total: 446ms	remaining: 179ms
112:	learn: 0.4841091	total: 450ms	remaining: 175ms
113:	learn: 0.4835586	total: 453ms	remaining: 171ms
114:	learn: 0.4829790	total: 457ms	remaining: 167ms
115:	learn: 0.4823679	total: 461ms	remaining: 163ms
116:	learn: 0.4818392	total: 464ms	remaining: 159ms
117:	learn: 0.4812188	total: 469ms	remaining: 155ms
118:	learn: 0.4800196	total: 473ms	remaining: 151ms
119:	learn: 

149:	learn: 0.4604434	total: 576ms	remaining: 26.9ms
150:	learn: 0.4601899	total: 579ms	remaining: 23ms
151:	learn: 0.4596874	total: 583ms	remaining: 19.2ms
152:	learn: 0.4589519	total: 587ms	remaining: 15.3ms
153:	learn: 0.4583689	total: 591ms	remaining: 11.5ms
154:	learn: 0.4578904	total: 594ms	remaining: 7.67ms
155:	learn: 0.4571651	total: 598ms	remaining: 3.83ms
156:	learn: 0.4566993	total: 602ms	remaining: 0us
0:	learn: 0.6723705	total: 10.4ms	remaining: 1.62s
1:	learn: 0.6553111	total: 15ms	remaining: 1.16s
2:	learn: 0.6415267	total: 19.1ms	remaining: 979ms
3:	learn: 0.6291752	total: 23.1ms	remaining: 884ms
4:	learn: 0.6194436	total: 26.9ms	remaining: 818ms
5:	learn: 0.6108060	total: 30.9ms	remaining: 778ms
6:	learn: 0.6037534	total: 34.7ms	remaining: 743ms
7:	learn: 0.5975739	total: 38.3ms	remaining: 714ms
8:	learn: 0.5914398	total: 42.1ms	remaining: 692ms
9:	learn: 0.5864645	total: 45.9ms	remaining: 675ms
10:	learn: 0.5825164	total: 49.6ms	remaining: 658ms
11:	learn: 0.5789578	

0:	learn: 0.6725759	total: 12.9ms	remaining: 2.01s
1:	learn: 0.6560866	total: 17.5ms	remaining: 1.35s
2:	learn: 0.6418593	total: 21.4ms	remaining: 1.1s
3:	learn: 0.6300052	total: 25.2ms	remaining: 963ms
4:	learn: 0.6203842	total: 28.8ms	remaining: 874ms
5:	learn: 0.6118583	total: 32.4ms	remaining: 814ms
6:	learn: 0.6044180	total: 35.9ms	remaining: 770ms
7:	learn: 0.5988443	total: 39.6ms	remaining: 737ms
8:	learn: 0.5927307	total: 43.3ms	remaining: 712ms
9:	learn: 0.5879586	total: 46.9ms	remaining: 690ms
10:	learn: 0.5840240	total: 50.6ms	remaining: 672ms
11:	learn: 0.5806353	total: 54.6ms	remaining: 660ms
12:	learn: 0.5773250	total: 58.4ms	remaining: 647ms
13:	learn: 0.5745540	total: 62ms	remaining: 633ms
14:	learn: 0.5721705	total: 65.7ms	remaining: 622ms
15:	learn: 0.5701044	total: 69.4ms	remaining: 611ms
16:	learn: 0.5680896	total: 73.2ms	remaining: 603ms
17:	learn: 0.5662040	total: 77.1ms	remaining: 596ms
18:	learn: 0.5645305	total: 80.8ms	remaining: 587ms
19:	learn: 0.5625244	tota

49:	learn: 0.5284017	total: 201ms	remaining: 430ms
50:	learn: 0.5278425	total: 204ms	remaining: 425ms
51:	learn: 0.5272746	total: 208ms	remaining: 420ms
52:	learn: 0.5267263	total: 211ms	remaining: 415ms
53:	learn: 0.5259693	total: 215ms	remaining: 410ms
54:	learn: 0.5242423	total: 219ms	remaining: 406ms
55:	learn: 0.5240314	total: 222ms	remaining: 400ms
56:	learn: 0.5234172	total: 226ms	remaining: 396ms
57:	learn: 0.5229978	total: 229ms	remaining: 391ms
58:	learn: 0.5216698	total: 233ms	remaining: 386ms
59:	learn: 0.5208900	total: 236ms	remaining: 382ms
60:	learn: 0.5205974	total: 240ms	remaining: 377ms
61:	learn: 0.5193915	total: 243ms	remaining: 373ms
62:	learn: 0.5188227	total: 247ms	remaining: 368ms
63:	learn: 0.5183325	total: 250ms	remaining: 364ms
64:	learn: 0.5179983	total: 254ms	remaining: 359ms
65:	learn: 0.5175313	total: 258ms	remaining: 355ms
66:	learn: 0.5166858	total: 261ms	remaining: 351ms
67:	learn: 0.5160452	total: 265ms	remaining: 347ms
68:	learn: 0.5152192	total: 269

102:	learn: 0.4900952	total: 393ms	remaining: 206ms
103:	learn: 0.4895506	total: 396ms	remaining: 202ms
104:	learn: 0.4889756	total: 400ms	remaining: 198ms
105:	learn: 0.4883200	total: 403ms	remaining: 194ms
106:	learn: 0.4879334	total: 407ms	remaining: 190ms
107:	learn: 0.4876194	total: 411ms	remaining: 186ms
108:	learn: 0.4871952	total: 414ms	remaining: 182ms
109:	learn: 0.4866931	total: 418ms	remaining: 178ms
110:	learn: 0.4857518	total: 421ms	remaining: 175ms
111:	learn: 0.4852222	total: 425ms	remaining: 171ms
112:	learn: 0.4841091	total: 429ms	remaining: 167ms
113:	learn: 0.4835586	total: 433ms	remaining: 163ms
114:	learn: 0.4829790	total: 436ms	remaining: 159ms
115:	learn: 0.4823679	total: 440ms	remaining: 156ms
116:	learn: 0.4818392	total: 444ms	remaining: 152ms
117:	learn: 0.4812188	total: 447ms	remaining: 148ms
118:	learn: 0.4800196	total: 451ms	remaining: 144ms
119:	learn: 0.4785166	total: 455ms	remaining: 140ms
120:	learn: 0.4773882	total: 459ms	remaining: 137ms
121:	learn: 

150:	learn: 0.4601899	total: 564ms	remaining: 22.4ms
151:	learn: 0.4596874	total: 568ms	remaining: 18.7ms
152:	learn: 0.4589519	total: 572ms	remaining: 14.9ms
153:	learn: 0.4583689	total: 575ms	remaining: 11.2ms
154:	learn: 0.4578904	total: 579ms	remaining: 7.47ms
155:	learn: 0.4571651	total: 583ms	remaining: 3.73ms
156:	learn: 0.4566993	total: 586ms	remaining: 0us


In [65]:
pd.DataFrame(model_scores).round(4)

Model Name  Accuracy train  \
0                                  LogisticRegression        0.819900   
1                              DecisionTreeClassifier        0.832200   
2                              RandomForestClassifier        0.833100   
3                                          GaussianNB        0.791100   
4                                         BernoulliNB        0.819500   
5                                  AdaBoostClassifier        0.829400   
6                          GradientBoostingClassifier        0.831200   
7                                       XGBClassifier        0.833100   
8   <catboost.core.CatBoostClassifier object at 0x...        0.832700   
9                                      LGBMClassifier        0.834700   
10                               KNeighborsClassifier        0.850200   
11                           LogisticRegression SMOTE        0.674800   
12                       DecisionTreeClassifier SMOTE        0.736500   
13                       RandomForestClassifier SMOTE        0.749700   
14                                   GaussianNB SMOTE        0.649400   
15                                  BernoulliNB SMOTE        0.666600   
16                           AdaBoostClassifier SMOTE        0.734100   
17                   GradientBoostingClassifier SMOTE        0.731800   
18                                XGBClassifier SMOTE        0.875500   
19  <catboost.core.CatBoostClassifier object at 0x...        0.799200   
20                               LGBMClassifier SMOTE        0.824100   
21                         KNeighborsClassifier SMOTE        0.846600   
22                          LogisticRegression ADASYN        0.646700   
23                      DecisionTreeClassifier ADASYN        0.718500   
24                      RandomForestClassifier ADASYN        0.731200   
25                                  GaussianNB ADASYN        0.580200   
26                                 BernoulliNB ADASYN        0.647000   
27                          AdaBoostClassifier ADASYN        0.722000   
28                  GradientBoostingClassifier ADASYN        0.714300   
29                               XGBClassifier ADASYN        0.876600   
30  <catboost.core.CatBoostClassifier object at 0x...        0.788000   
31                              LGBMClassifier ADASYN        0.812600   
32                        KNeighborsClassifier ADASYN        0.834400   

    Precision train  Recall train  F1 train  F1 Avg Weighted train  \
0          0.758000      0.158800  0.262600               0.769200   
1          0.767700      0.242600  0.368700               0.795300   
2          0.773700      0.245500  0.372700               0.796500   
3          0.472400      0.292600  0.361400               0.771400   
4          0.685800      0.195700  0.304600               0.776800   
5          0.730700      0.245500  0.367600               0.793600   
6          0.763000      0.238000  0.362800               0.793700   
7          0.761000      0.252900  0.379600               0.797800   
8          0.767200      0.246100  0.372700               0.796300   
9          0.781700      0.251600  0.380700               0.798800   
10         0.737300      0.401400  0.519800               0.832200   
11         0.703300      0.604800  0.650300               0.673200   
12         0.739800      0.729500  0.734600               0.736500   
13         0.726000      0.802100  0.762200               0.749000   
14         0.641200      0.678500  0.659300               0.649100   
15         0.683900      0.619400  0.650100               0.665800   
16         0.710900      0.789000  0.747900               0.733300   
17         0.699100      0.814000  0.752200               0.730000   
18         0.956400      0.786800  0.863400               0.874500   
19         0.803700      0.791800  0.797700               0.799200   
20         0.841000      0.799200  0.819600               0.824000   
21         0.823100 

In [66]:
from imblearn.combine import SMOTEENN
from collections import Counter

counter = Counter(y_train)
print('Before', counter)

enn = SMOTEENN(random_state=10)
X_train_enn, y_train_enn = enn.fit_resample(X_train, y_train)

counter = Counter(y_train_enn)
print('After', counter)

Before Counter({0: 61743, 1: 15623})
After Counter({1: 36142, 0: 35246})


In [67]:
lr_pipeline = Pipeline([
    ('lr_model', LogisticRegression(**rsearch_lr.best_params_))
])

In [68]:
dt_pipeline = Pipeline([
    ('dt_model', DecisionTreeClassifier(**rsearch_dt.best_params_,random_state=42))
])

In [69]:
rf_pipeline = Pipeline([
    ('rf_model', RandomForestClassifier(**rsearch_rf.best_params_,random_state=42))
])

In [70]:
gnb_pipeline = Pipeline([
    ('gnb_model', GaussianNB())
])

In [71]:
bnb_pipeline = Pipeline([
    ('bnb_model', BernoulliNB())
])

In [72]:
knn_pipeline = Pipeline([
    ('knn_model', KNeighborsClassifier())
])

In [73]:
ada_pipeline = Pipeline([
    ('rf_model', AdaBoostClassifier(**rsearch_ada.best_params_, random_state = 42))
])

In [74]:
gb_pipeline = Pipeline([
    ('rf_model', GradientBoostingClassifier(**rsearch_gb.best_params_, random_state = 42))
])

In [75]:
cb_pipeline = Pipeline([
    ('cb_model', CatBoostClassifier(**rsearch_cb.best_params_, random_state = 42))
])

In [76]:
lgbm_pipeline = Pipeline([
    ('lgbm_model', LGBMClassifier(**rsearch_lgbm.best_params_, random_state = 42))
])

In [77]:
xgb_pipeline = Pipeline([
    ('rf_model', XGBClassifier(**rsearch_xgb.best_params_, random_state = 42))
])

In [78]:
pipe_all = [lr_pipeline, dt_pipeline, rf_pipeline, gnb_pipeline, bnb_pipeline, ada_pipeline, gb_pipeline, xgb_pipeline, cb_pipeline, lgbm_pipeline,
            knn_pipeline]
            
for pipe in pipe_all:
  pipe.fit(X_train_enn, y_train_enn)

0:	learn: 0.6413101	total: 29.4ms	remaining: 4.59s
1:	learn: 0.5989567	total: 32.8ms	remaining: 2.54s
2:	learn: 0.5644966	total: 36.2ms	remaining: 1.86s
3:	learn: 0.5345919	total: 39.6ms	remaining: 1.51s
4:	learn: 0.5093332	total: 43.3ms	remaining: 1.31s
5:	learn: 0.4874125	total: 46.7ms	remaining: 1.18s
6:	learn: 0.4684814	total: 50.2ms	remaining: 1.08s
7:	learn: 0.4518616	total: 53.7ms	remaining: 1s
8:	learn: 0.4379983	total: 57.2ms	remaining: 941ms
9:	learn: 0.4257211	total: 60.4ms	remaining: 888ms
10:	learn: 0.4146320	total: 64ms	remaining: 850ms
11:	learn: 0.4044666	total: 67.5ms	remaining: 815ms
12:	learn: 0.3958472	total: 70.8ms	remaining: 785ms
13:	learn: 0.3881740	total: 74.4ms	remaining: 760ms
14:	learn: 0.3813826	total: 77.6ms	remaining: 735ms
15:	learn: 0.3755955	total: 81ms	remaining: 714ms
16:	learn: 0.3706286	total: 84.6ms	remaining: 697ms
17:	learn: 0.3657959	total: 88.4ms	remaining: 682ms
18:	learn: 0.3613824	total: 91.8ms	remaining: 667ms
19:	learn: 0.3570600	total: 9

In [79]:
for model in pipe_all:
    
    model_scores['Model Name'].append(str(model[0]).split('(')[0] + " ENN")
    
    model_scores['Accuracy train'].append(model.score(X_train_enn, y_train_enn))
    pred_tr = model.predict(X_train_enn)
    prob_tr = model.predict_proba(X_train_enn)[:,1]
    model_scores['Precision train'].append(precision_score(y_train_enn, pred_tr))
    model_scores['Recall train'].append(recall_score(y_train_enn, pred_tr))
    model_scores['F1 train'].append(f1_score(y_train_enn, pred_tr))
    model_scores['F1 Avg Weighted train'].append(f1_score(y_train_enn, pred_tr, average = 'weighted'))
    model_scores['ROC AUC train'].append(roc_auc_score(y_train_enn, prob_tr))
    
    model_scores['Accuracy test'].append(model.score(X_test, y_test))
    pred_ts = model.predict(X_test)
    prob_ts = model.predict_proba(X_test)[:,1]
    model_scores['Precision test'].append(precision_score(y_test, pred_ts))
    model_scores['Recall test'].append(recall_score(y_test, pred_ts))
    model_scores['F1 test'].append(f1_score(y_test, pred_ts))
    model_scores['F1 Avg Weighted test'].append(f1_score(y_test, pred_ts, average = 'weighted'))
    model_scores['ROC AUC test'].append(roc_auc_score(y_test, prob_ts))

    model_scores['CV-5-Mean'].append(cross_val_score(model,X_train_enn,y_train_enn,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').mean())
    model_scores['CV-5-SD'].append(cross_val_score(model,X_train_enn,y_train_enn,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').std())

0:	learn: 0.6415160	total: 5.13ms	remaining: 801ms
1:	learn: 0.5993058	total: 8.34ms	remaining: 646ms
2:	learn: 0.5651501	total: 11.1ms	remaining: 571ms
3:	learn: 0.5353500	total: 14.1ms	remaining: 538ms
4:	learn: 0.5100831	total: 16.9ms	remaining: 514ms
5:	learn: 0.4880538	total: 19.7ms	remaining: 496ms
6:	learn: 0.4689559	total: 22.4ms	remaining: 480ms
7:	learn: 0.4524122	total: 25.1ms	remaining: 467ms
8:	learn: 0.4385510	total: 27.8ms	remaining: 457ms
9:	learn: 0.4262371	total: 30.5ms	remaining: 449ms
10:	learn: 0.4151291	total: 33.7ms	remaining: 447ms
11:	learn: 0.4052602	total: 36.6ms	remaining: 442ms
12:	learn: 0.3965007	total: 39.4ms	remaining: 436ms
13:	learn: 0.3886676	total: 42ms	remaining: 429ms
14:	learn: 0.3821519	total: 44.7ms	remaining: 423ms
15:	learn: 0.3763696	total: 47.5ms	remaining: 418ms
16:	learn: 0.3712562	total: 50.3ms	remaining: 414ms
17:	learn: 0.3657721	total: 53ms	remaining: 410ms
18:	learn: 0.3620156	total: 55.7ms	remaining: 405ms
19:	learn: 0.3575211	total

66:	learn: 0.3032612	total: 193ms	remaining: 259ms
67:	learn: 0.3029333	total: 195ms	remaining: 256ms
68:	learn: 0.3022038	total: 198ms	remaining: 253ms
69:	learn: 0.3018914	total: 201ms	remaining: 249ms
70:	learn: 0.3014323	total: 203ms	remaining: 246ms
71:	learn: 0.3007350	total: 206ms	remaining: 243ms
72:	learn: 0.3004285	total: 209ms	remaining: 240ms
73:	learn: 0.3001060	total: 211ms	remaining: 237ms
74:	learn: 0.2997614	total: 214ms	remaining: 234ms
75:	learn: 0.2987614	total: 217ms	remaining: 231ms
76:	learn: 0.2985666	total: 219ms	remaining: 228ms
77:	learn: 0.2981024	total: 222ms	remaining: 225ms
78:	learn: 0.2977757	total: 225ms	remaining: 222ms
79:	learn: 0.2972262	total: 227ms	remaining: 219ms
80:	learn: 0.2970362	total: 230ms	remaining: 216ms
81:	learn: 0.2965733	total: 233ms	remaining: 213ms
82:	learn: 0.2962824	total: 235ms	remaining: 210ms
83:	learn: 0.2959861	total: 238ms	remaining: 207ms
84:	learn: 0.2957454	total: 241ms	remaining: 204ms
85:	learn: 0.2949257	total: 243

122:	learn: 0.2828247	total: 366ms	remaining: 101ms
123:	learn: 0.2817225	total: 369ms	remaining: 98.3ms
124:	learn: 0.2813766	total: 373ms	remaining: 95.4ms
125:	learn: 0.2809354	total: 376ms	remaining: 92.4ms
126:	learn: 0.2799065	total: 379ms	remaining: 89.5ms
127:	learn: 0.2797223	total: 381ms	remaining: 86.4ms
128:	learn: 0.2787416	total: 385ms	remaining: 83.5ms
129:	learn: 0.2780701	total: 388ms	remaining: 80.5ms
130:	learn: 0.2772351	total: 390ms	remaining: 77.5ms
131:	learn: 0.2765747	total: 393ms	remaining: 74.5ms
132:	learn: 0.2763253	total: 396ms	remaining: 71.5ms
133:	learn: 0.2754967	total: 399ms	remaining: 68.5ms
134:	learn: 0.2746744	total: 402ms	remaining: 65.5ms
135:	learn: 0.2743251	total: 405ms	remaining: 62.6ms
136:	learn: 0.2735139	total: 408ms	remaining: 59.6ms
137:	learn: 0.2728054	total: 411ms	remaining: 56.6ms
138:	learn: 0.2723489	total: 414ms	remaining: 53.6ms
139:	learn: 0.2721259	total: 417ms	remaining: 50.6ms
140:	learn: 0.2717548	total: 419ms	remaining: 4

130:	learn: 0.2752719	total: 359ms	remaining: 71.3ms
131:	learn: 0.2747072	total: 362ms	remaining: 68.5ms
132:	learn: 0.2744944	total: 365ms	remaining: 65.8ms
133:	learn: 0.2741372	total: 367ms	remaining: 63.1ms
134:	learn: 0.2738572	total: 370ms	remaining: 60.3ms
135:	learn: 0.2735909	total: 373ms	remaining: 57.5ms
136:	learn: 0.2728691	total: 375ms	remaining: 54.8ms
137:	learn: 0.2721225	total: 378ms	remaining: 52.1ms
138:	learn: 0.2718505	total: 381ms	remaining: 49.4ms
139:	learn: 0.2713699	total: 384ms	remaining: 46.6ms
140:	learn: 0.2709377	total: 386ms	remaining: 43.9ms
141:	learn: 0.2705207	total: 389ms	remaining: 41.1ms
142:	learn: 0.2700701	total: 392ms	remaining: 38.4ms
143:	learn: 0.2699111	total: 394ms	remaining: 35.6ms
144:	learn: 0.2697335	total: 397ms	remaining: 32.9ms
145:	learn: 0.2694756	total: 400ms	remaining: 30.1ms
146:	learn: 0.2692337	total: 403ms	remaining: 27.4ms
147:	learn: 0.2684696	total: 405ms	remaining: 24.6ms
148:	learn: 0.2683014	total: 408ms	remaining: 

133:	learn: 0.2740615	total: 384ms	remaining: 65.8ms
134:	learn: 0.2738151	total: 386ms	remaining: 63ms
135:	learn: 0.2732988	total: 389ms	remaining: 60.1ms
136:	learn: 0.2730169	total: 392ms	remaining: 57.2ms
137:	learn: 0.2728669	total: 394ms	remaining: 54.3ms
138:	learn: 0.2726171	total: 397ms	remaining: 51.4ms
139:	learn: 0.2722565	total: 400ms	remaining: 48.5ms
140:	learn: 0.2719481	total: 402ms	remaining: 45.7ms
141:	learn: 0.2710197	total: 405ms	remaining: 42.8ms
142:	learn: 0.2707960	total: 408ms	remaining: 40ms
143:	learn: 0.2704387	total: 411ms	remaining: 37.1ms
144:	learn: 0.2703383	total: 413ms	remaining: 34.2ms
145:	learn: 0.2700763	total: 416ms	remaining: 31.3ms
146:	learn: 0.2697762	total: 419ms	remaining: 28.5ms
147:	learn: 0.2695811	total: 421ms	remaining: 25.6ms
148:	learn: 0.2692585	total: 424ms	remaining: 22.8ms
149:	learn: 0.2690511	total: 427ms	remaining: 19.9ms
150:	learn: 0.2684732	total: 430ms	remaining: 17.1ms
151:	learn: 0.2683028	total: 432ms	remaining: 14.2

0:	learn: 0.6413738	total: 13.5ms	remaining: 2.11s
1:	learn: 0.5997875	total: 16.6ms	remaining: 1.29s
2:	learn: 0.5655761	total: 19.4ms	remaining: 998ms
3:	learn: 0.5354795	total: 22.2ms	remaining: 848ms
4:	learn: 0.5100788	total: 25ms	remaining: 759ms
5:	learn: 0.4881037	total: 27.9ms	remaining: 702ms
6:	learn: 0.4689452	total: 30.7ms	remaining: 659ms
7:	learn: 0.4522958	total: 33.4ms	remaining: 623ms
8:	learn: 0.4381476	total: 36.1ms	remaining: 594ms
9:	learn: 0.4258143	total: 38.9ms	remaining: 572ms
10:	learn: 0.4147187	total: 41.8ms	remaining: 555ms
11:	learn: 0.4048973	total: 44.6ms	remaining: 539ms
12:	learn: 0.3964428	total: 47.2ms	remaining: 523ms
13:	learn: 0.3884627	total: 49.9ms	remaining: 510ms
14:	learn: 0.3818376	total: 52.6ms	remaining: 498ms
15:	learn: 0.3759500	total: 55.4ms	remaining: 488ms
16:	learn: 0.3709164	total: 58.2ms	remaining: 479ms
17:	learn: 0.3656632	total: 61ms	remaining: 471ms
18:	learn: 0.3611466	total: 63.9ms	remaining: 464ms
19:	learn: 0.3567793	total

67:	learn: 0.3047015	total: 200ms	remaining: 261ms
68:	learn: 0.3042407	total: 202ms	remaining: 258ms
69:	learn: 0.3038256	total: 205ms	remaining: 255ms
70:	learn: 0.3034546	total: 208ms	remaining: 251ms
71:	learn: 0.3030465	total: 210ms	remaining: 248ms
72:	learn: 0.3022987	total: 213ms	remaining: 245ms
73:	learn: 0.3018548	total: 215ms	remaining: 242ms
74:	learn: 0.3015247	total: 218ms	remaining: 239ms
75:	learn: 0.3010738	total: 221ms	remaining: 236ms
76:	learn: 0.3003795	total: 224ms	remaining: 233ms
77:	learn: 0.2997041	total: 227ms	remaining: 230ms
78:	learn: 0.2993397	total: 229ms	remaining: 226ms
79:	learn: 0.2989021	total: 232ms	remaining: 223ms
80:	learn: 0.2987187	total: 235ms	remaining: 220ms
81:	learn: 0.2984310	total: 237ms	remaining: 217ms
82:	learn: 0.2981296	total: 240ms	remaining: 214ms
83:	learn: 0.2978035	total: 242ms	remaining: 211ms
84:	learn: 0.2965631	total: 245ms	remaining: 208ms
85:	learn: 0.2963205	total: 248ms	remaining: 204ms
86:	learn: 0.2957785	total: 250

136:	learn: 0.2728691	total: 379ms	remaining: 55.4ms
137:	learn: 0.2721225	total: 382ms	remaining: 52.6ms
138:	learn: 0.2718505	total: 385ms	remaining: 49.9ms
139:	learn: 0.2713699	total: 388ms	remaining: 47.1ms
140:	learn: 0.2709377	total: 390ms	remaining: 44.3ms
141:	learn: 0.2705207	total: 393ms	remaining: 41.5ms
142:	learn: 0.2700701	total: 396ms	remaining: 38.7ms
143:	learn: 0.2699111	total: 398ms	remaining: 36ms
144:	learn: 0.2697335	total: 401ms	remaining: 33.2ms
145:	learn: 0.2694756	total: 403ms	remaining: 30.4ms
146:	learn: 0.2692337	total: 407ms	remaining: 27.7ms
147:	learn: 0.2684696	total: 409ms	remaining: 24.9ms
148:	learn: 0.2683014	total: 412ms	remaining: 22.1ms
149:	learn: 0.2680320	total: 415ms	remaining: 19.4ms
150:	learn: 0.2678158	total: 418ms	remaining: 16.6ms
151:	learn: 0.2672842	total: 420ms	remaining: 13.8ms
152:	learn: 0.2671523	total: 423ms	remaining: 11.1ms
153:	learn: 0.2669178	total: 425ms	remaining: 8.29ms
154:	learn: 0.2667400	total: 428ms	remaining: 5.

In [80]:
pd.DataFrame(model_scores).round(4)

Model Name  Accuracy train  \
0                                  LogisticRegression        0.819900   
1                              DecisionTreeClassifier        0.832200   
2                              RandomForestClassifier        0.833100   
3                                          GaussianNB        0.791100   
4                                         BernoulliNB        0.819500   
5                                  AdaBoostClassifier        0.829400   
6                          GradientBoostingClassifier        0.831200   
7                                       XGBClassifier        0.833100   
8   <catboost.core.CatBoostClassifier object at 0x...        0.832700   
9                                      LGBMClassifier        0.834700   
10                               KNeighborsClassifier        0.850200   
11                           LogisticRegression SMOTE        0.674800   
12                       DecisionTreeClassifier SMOTE        0.736500   
13                       RandomForestClassifier SMOTE        0.749700   
14                                   GaussianNB SMOTE        0.649400   
15                                  BernoulliNB SMOTE        0.666600   
16                           AdaBoostClassifier SMOTE        0.734100   
17                   GradientBoostingClassifier SMOTE        0.731800   
18                                XGBClassifier SMOTE        0.875500   
19  <catboost.core.CatBoostClassifier object at 0x...        0.799200   
20                               LGBMClassifier SMOTE        0.824100   
21                         KNeighborsClassifier SMOTE        0.846600   
22                          LogisticRegression ADASYN        0.646700   
23                      DecisionTreeClassifier ADASYN        0.718500   
24                      RandomForestClassifier ADASYN        0.731200   
25                                  GaussianNB ADASYN        0.580200   
26                                 BernoulliNB ADASYN        0.647000   
27                          AdaBoostClassifier ADASYN        0.722000   
28                  GradientBoostingClassifier ADASYN        0.714300   
29                               XGBClassifier ADASYN        0.876600   
30  <catboost.core.CatBoostClassifier object at 0x...        0.788000   
31                              LGBMClassifier ADASYN        0.812600   
32                        KNeighborsClassifier ADASYN        0.834400   
33                             LogisticRegression ENN        0.798200   
34                         DecisionTreeClassifier ENN        0.857900   
35                         RandomForestClassifier ENN        0.872500   
36                                     GaussianNB ENN        0.765200   
37                                    BernoulliNB ENN        0.780900   
38                             AdaBoostClassifier ENN        0.852000   
39                     GradientBoostingClassifier ENN        0.844500   
40                                  XGBClassifier ENN        0.931300   
41  <catboost.core.CatBoostClassifier object at 0x...        0.887300   
42                                 LGBMClassifier ENN        0.913700   
43                           KNeighborsClassifier ENN        0.976300   

    Precision train  Recall train  F1 train  F1 Avg Weighted train  \
0          0.758000      0.158800  0.262600               0.769200   
1          0.767700      0.242600  0.368700               0.795300   
2          0.773700      0.245500  0.372700               0.796500   
3          0.472400      0.292600  0.361400               0.771400   
4          0.685800      0.195700  0.304600               0.776800   
5          0.730700      0.245500  0.367600               0.793600   
6          0.763000      0.238000  0.362800               0.793700   
7          0.761000      0.252900  0.379600               0.797800   
8          0.767200      0.246100  0.372700               0.796300   
9          0.781700      0.251600  0.380700              

In [81]:
from imblearn.combine import SMOTEENN
from collections import Counter
from imblearn.under_sampling import EditedNearestNeighbours

counter = Counter(y_train)
print('Before', counter)

smote = SMOTE(random_state=10)
enn = EditedNearestNeighbours()

se = SMOTEENN(random_state=10, smote=smote, enn=enn)
X_train_se, y_train_se = se.fit_resample(X_train, y_train)

counter = Counter(y_train_se)
print('After', counter)

Before Counter({0: 61743, 1: 15623})
After Counter({0: 61743, 1: 36142})


In [82]:
lr_pipeline = Pipeline([
    ('lr_model', LogisticRegression(**rsearch_lr.best_params_))
])

In [83]:
dt_pipeline = Pipeline([
    ('dt_model', DecisionTreeClassifier(**rsearch_dt.best_params_,random_state=42))
])

In [84]:
rf_pipeline = Pipeline([
    ('rf_model', RandomForestClassifier(**rsearch_rf.best_params_,random_state=42))
])

In [85]:
gnb_pipeline = Pipeline([
    ('gnb_model', GaussianNB())
])

In [86]:
bnb_pipeline = Pipeline([
    ('bnb_model', BernoulliNB())
])

In [87]:
knn_pipeline = Pipeline([
    ('knn_model', KNeighborsClassifier())
])

In [88]:
ada_pipeline = Pipeline([
    ('rf_model', AdaBoostClassifier(**rsearch_ada.best_params_, random_state = 42))
])

In [89]:
gb_pipeline = Pipeline([
    ('rf_model', GradientBoostingClassifier(**rsearch_gb.best_params_, random_state = 42))
])

In [90]:
cb_pipeline = Pipeline([
    ('cb_model', CatBoostClassifier(**rsearch_cb.best_params_, random_state = 42))
])

In [91]:
lgbm_pipeline = Pipeline([
    ('lgbm_model', LGBMClassifier(**rsearch_lgbm.best_params_, random_state = 42))
])

In [92]:
xgb_pipeline = Pipeline([
    ('rf_model', XGBClassifier(**rsearch_xgb.best_params_, random_state = 42))
])

In [93]:
pipe_all = [lr_pipeline, dt_pipeline, rf_pipeline, gnb_pipeline, bnb_pipeline, ada_pipeline, gb_pipeline, xgb_pipeline, cb_pipeline, lgbm_pipeline,
            knn_pipeline]
            
for pipe in pipe_all:
  pipe.fit(X_train_se, y_train_se)

0:	learn: 0.6542749	total: 4.61ms	remaining: 720ms
1:	learn: 0.6226542	total: 8.63ms	remaining: 669ms
2:	learn: 0.5965617	total: 12.5ms	remaining: 642ms
3:	learn: 0.5743382	total: 16.4ms	remaining: 626ms
4:	learn: 0.5552758	total: 20.4ms	remaining: 620ms
5:	learn: 0.5392133	total: 24.3ms	remaining: 611ms
6:	learn: 0.5251895	total: 28.4ms	remaining: 609ms
7:	learn: 0.5135475	total: 32.5ms	remaining: 606ms
8:	learn: 0.5025377	total: 36.8ms	remaining: 606ms
9:	learn: 0.4934720	total: 40.7ms	remaining: 598ms
10:	learn: 0.4852750	total: 44.4ms	remaining: 590ms
11:	learn: 0.4774536	total: 48.5ms	remaining: 586ms
12:	learn: 0.4718652	total: 52.1ms	remaining: 577ms
13:	learn: 0.4658180	total: 55.6ms	remaining: 568ms
14:	learn: 0.4605230	total: 59.5ms	remaining: 563ms
15:	learn: 0.4554327	total: 63.1ms	remaining: 556ms
16:	learn: 0.4516806	total: 66.8ms	remaining: 550ms
17:	learn: 0.4474157	total: 70.5ms	remaining: 545ms
18:	learn: 0.4433302	total: 74.2ms	remaining: 539ms
19:	learn: 0.4400771	t

In [94]:
for model in pipe_all:
    
    model_scores['Model Name'].append(str(model[0]).split('(')[0] + " SMOTE + ENN")
    
    model_scores['Accuracy train'].append(model.score(X_train_se, y_train_se))
    pred_tr = model.predict(X_train_se)
    prob_tr = model.predict_proba(X_train_se)[:,1]
    model_scores['Precision train'].append(precision_score(y_train_se, pred_tr))
    model_scores['Recall train'].append(recall_score(y_train_se, pred_tr))
    model_scores['F1 train'].append(f1_score(y_train_se, pred_tr))
    model_scores['F1 Avg Weighted train'].append(f1_score(y_train_se, pred_tr, average = 'weighted'))
    model_scores['ROC AUC train'].append(roc_auc_score(y_train_se, prob_tr))
    
    model_scores['Accuracy test'].append(model.score(X_test, y_test))
    pred_ts = model.predict(X_test)
    prob_ts = model.predict_proba(X_test)[:,1]
    model_scores['Precision test'].append(precision_score(y_test, pred_ts))
    model_scores['Recall test'].append(recall_score(y_test, pred_ts))
    model_scores['F1 test'].append(f1_score(y_test, pred_ts))
    model_scores['F1 Avg Weighted test'].append(f1_score(y_test, pred_ts, average = 'weighted'))
    model_scores['ROC AUC test'].append(roc_auc_score(y_test, prob_ts))

    model_scores['CV-5-Mean'].append(cross_val_score(model,X_train_se,y_train_se,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').mean())
    model_scores['CV-5-SD'].append(cross_val_score(model,X_train_se,y_train_se,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').std())

0:	learn: 0.6543483	total: 15.7ms	remaining: 2.45s
1:	learn: 0.6230229	total: 19.7ms	remaining: 1.53s
2:	learn: 0.5968022	total: 23.1ms	remaining: 1.19s
3:	learn: 0.5743961	total: 26.4ms	remaining: 1.01s
4:	learn: 0.5554852	total: 29.9ms	remaining: 908ms
5:	learn: 0.5392388	total: 33.2ms	remaining: 837ms
6:	learn: 0.5254162	total: 36.4ms	remaining: 780ms
7:	learn: 0.5142882	total: 39.5ms	remaining: 736ms
8:	learn: 0.5032459	total: 42.9ms	remaining: 706ms
9:	learn: 0.4942088	total: 46.1ms	remaining: 678ms
10:	learn: 0.4861403	total: 49.4ms	remaining: 656ms
11:	learn: 0.4785058	total: 52.7ms	remaining: 637ms
12:	learn: 0.4726556	total: 56.1ms	remaining: 622ms
13:	learn: 0.4665025	total: 59.6ms	remaining: 609ms
14:	learn: 0.4611387	total: 63ms	remaining: 596ms
15:	learn: 0.4561089	total: 66.2ms	remaining: 584ms
16:	learn: 0.4525971	total: 69.6ms	remaining: 573ms
17:	learn: 0.4485214	total: 72.8ms	remaining: 562ms
18:	learn: 0.4443078	total: 76.1ms	remaining: 553ms
19:	learn: 0.4408999	tot

56:	learn: 0.3915017	total: 199ms	remaining: 349ms
57:	learn: 0.3911370	total: 203ms	remaining: 346ms
58:	learn: 0.3907954	total: 206ms	remaining: 342ms
59:	learn: 0.3903952	total: 210ms	remaining: 339ms
60:	learn: 0.3884107	total: 214ms	remaining: 337ms
61:	learn: 0.3872453	total: 218ms	remaining: 334ms
62:	learn: 0.3868899	total: 221ms	remaining: 330ms
63:	learn: 0.3863792	total: 225ms	remaining: 327ms
64:	learn: 0.3859927	total: 228ms	remaining: 323ms
65:	learn: 0.3854596	total: 232ms	remaining: 319ms
66:	learn: 0.3838903	total: 235ms	remaining: 316ms
67:	learn: 0.3834148	total: 239ms	remaining: 312ms
68:	learn: 0.3830393	total: 242ms	remaining: 308ms
69:	learn: 0.3823399	total: 245ms	remaining: 305ms
70:	learn: 0.3816033	total: 248ms	remaining: 301ms
71:	learn: 0.3811662	total: 252ms	remaining: 297ms
72:	learn: 0.3805932	total: 255ms	remaining: 293ms
73:	learn: 0.3802798	total: 258ms	remaining: 289ms
74:	learn: 0.3799264	total: 261ms	remaining: 286ms
75:	learn: 0.3790835	total: 265

110:	learn: 0.3699173	total: 360ms	remaining: 149ms
111:	learn: 0.3695829	total: 363ms	remaining: 146ms
112:	learn: 0.3691536	total: 367ms	remaining: 143ms
113:	learn: 0.3686899	total: 370ms	remaining: 140ms
114:	learn: 0.3682329	total: 374ms	remaining: 137ms
115:	learn: 0.3681100	total: 378ms	remaining: 134ms
116:	learn: 0.3663870	total: 381ms	remaining: 130ms
117:	learn: 0.3658783	total: 384ms	remaining: 127ms
118:	learn: 0.3655507	total: 387ms	remaining: 124ms
119:	learn: 0.3651723	total: 391ms	remaining: 120ms
120:	learn: 0.3648162	total: 394ms	remaining: 117ms
121:	learn: 0.3643134	total: 397ms	remaining: 114ms
122:	learn: 0.3638009	total: 400ms	remaining: 111ms
123:	learn: 0.3623804	total: 403ms	remaining: 107ms
124:	learn: 0.3621704	total: 407ms	remaining: 104ms
125:	learn: 0.3606148	total: 410ms	remaining: 101ms
126:	learn: 0.3600223	total: 413ms	remaining: 97.6ms
127:	learn: 0.3599242	total: 416ms	remaining: 94.3ms
128:	learn: 0.3596481	total: 419ms	remaining: 91ms
129:	learn:

150:	learn: 0.3425895	total: 561ms	remaining: 22.3ms
151:	learn: 0.3419210	total: 565ms	remaining: 18.6ms
152:	learn: 0.3415369	total: 569ms	remaining: 14.9ms
153:	learn: 0.3410755	total: 573ms	remaining: 11.2ms
154:	learn: 0.3406503	total: 577ms	remaining: 7.45ms
155:	learn: 0.3403240	total: 581ms	remaining: 3.73ms
156:	learn: 0.3397479	total: 585ms	remaining: 0us
0:	learn: 0.6543645	total: 23.2ms	remaining: 3.62s
1:	learn: 0.6231195	total: 26.9ms	remaining: 2.09s
2:	learn: 0.5971116	total: 30.2ms	remaining: 1.55s
3:	learn: 0.5748375	total: 33.8ms	remaining: 1.29s
4:	learn: 0.5558734	total: 37.8ms	remaining: 1.15s
5:	learn: 0.5398319	total: 41.6ms	remaining: 1.05s
6:	learn: 0.5262293	total: 45.4ms	remaining: 972ms
7:	learn: 0.5146688	total: 49ms	remaining: 912ms
8:	learn: 0.5040956	total: 52.6ms	remaining: 865ms
9:	learn: 0.4954986	total: 56.1ms	remaining: 825ms
10:	learn: 0.4864279	total: 60ms	remaining: 797ms
11:	learn: 0.4786865	total: 63.4ms	remaining: 766ms
12:	learn: 0.4728692	t

153:	learn: 0.3404617	total: 557ms	remaining: 10.8ms
154:	learn: 0.3400674	total: 560ms	remaining: 7.23ms
155:	learn: 0.3397129	total: 564ms	remaining: 3.62ms
156:	learn: 0.3387309	total: 568ms	remaining: 0us
0:	learn: 0.6543483	total: 10.1ms	remaining: 1.57s
1:	learn: 0.6230229	total: 14.3ms	remaining: 1.1s
2:	learn: 0.5968022	total: 18.4ms	remaining: 942ms
3:	learn: 0.5743961	total: 22.3ms	remaining: 852ms
4:	learn: 0.5554852	total: 26.1ms	remaining: 793ms
5:	learn: 0.5392388	total: 29.6ms	remaining: 746ms
6:	learn: 0.5254162	total: 33.5ms	remaining: 718ms
7:	learn: 0.5142882	total: 36.9ms	remaining: 687ms
8:	learn: 0.5032459	total: 40.8ms	remaining: 670ms
9:	learn: 0.4942088	total: 44.3ms	remaining: 651ms
10:	learn: 0.4861403	total: 48.3ms	remaining: 641ms
11:	learn: 0.4785058	total: 52.3ms	remaining: 632ms
12:	learn: 0.4726556	total: 55.9ms	remaining: 619ms
13:	learn: 0.4665025	total: 59.8ms	remaining: 610ms
14:	learn: 0.4611387	total: 63.6ms	remaining: 602ms
15:	learn: 0.4561089	t

1:	learn: 0.6228229	total: 31.8ms	remaining: 2.46s
2:	learn: 0.5964149	total: 35.7ms	remaining: 1.83s
3:	learn: 0.5739098	total: 39.5ms	remaining: 1.51s
4:	learn: 0.5549257	total: 43.4ms	remaining: 1.32s
5:	learn: 0.5386535	total: 47.3ms	remaining: 1.19s
6:	learn: 0.5246359	total: 52.2ms	remaining: 1.12s
7:	learn: 0.5131008	total: 57.1ms	remaining: 1.06s
8:	learn: 0.5021023	total: 61.4ms	remaining: 1.01s
9:	learn: 0.4929488	total: 65.2ms	remaining: 958ms
10:	learn: 0.4844508	total: 69.5ms	remaining: 923ms
11:	learn: 0.4769149	total: 73.9ms	remaining: 893ms
12:	learn: 0.4710868	total: 77.9ms	remaining: 862ms
13:	learn: 0.4649940	total: 82.1ms	remaining: 839ms
14:	learn: 0.4596928	total: 86.2ms	remaining: 816ms
15:	learn: 0.4546082	total: 90.3ms	remaining: 796ms
16:	learn: 0.4511084	total: 94.9ms	remaining: 781ms
17:	learn: 0.4468627	total: 98.5ms	remaining: 761ms
18:	learn: 0.4427045	total: 103ms	remaining: 749ms
19:	learn: 0.4391875	total: 108ms	remaining: 737ms
20:	learn: 0.4363531	to

53:	learn: 0.3961749	total: 185ms	remaining: 353ms
54:	learn: 0.3955508	total: 189ms	remaining: 351ms
55:	learn: 0.3951566	total: 193ms	remaining: 348ms
56:	learn: 0.3945168	total: 197ms	remaining: 346ms
57:	learn: 0.3941374	total: 201ms	remaining: 342ms
58:	learn: 0.3937472	total: 204ms	remaining: 339ms
59:	learn: 0.3934164	total: 208ms	remaining: 336ms
60:	learn: 0.3927621	total: 212ms	remaining: 333ms
61:	learn: 0.3915509	total: 216ms	remaining: 331ms
62:	learn: 0.3911218	total: 220ms	remaining: 328ms
63:	learn: 0.3905885	total: 224ms	remaining: 326ms
64:	learn: 0.3901387	total: 228ms	remaining: 323ms
65:	learn: 0.3896090	total: 232ms	remaining: 320ms
66:	learn: 0.3887466	total: 236ms	remaining: 318ms
67:	learn: 0.3884217	total: 240ms	remaining: 315ms
68:	learn: 0.3879909	total: 244ms	remaining: 312ms
69:	learn: 0.3871006	total: 248ms	remaining: 308ms
70:	learn: 0.3868090	total: 252ms	remaining: 306ms
71:	learn: 0.3862393	total: 257ms	remaining: 303ms
72:	learn: 0.3852916	total: 260

100:	learn: 0.3716161	total: 403ms	remaining: 224ms
101:	learn: 0.3712425	total: 407ms	remaining: 219ms
102:	learn: 0.3710666	total: 410ms	remaining: 215ms
103:	learn: 0.3708227	total: 413ms	remaining: 211ms
104:	learn: 0.3704262	total: 417ms	remaining: 206ms
105:	learn: 0.3700693	total: 420ms	remaining: 202ms
106:	learn: 0.3693648	total: 424ms	remaining: 198ms
107:	learn: 0.3689224	total: 427ms	remaining: 194ms
108:	learn: 0.3688008	total: 430ms	remaining: 190ms
109:	learn: 0.3679419	total: 434ms	remaining: 185ms
110:	learn: 0.3676370	total: 437ms	remaining: 181ms
111:	learn: 0.3673426	total: 440ms	remaining: 177ms
112:	learn: 0.3668233	total: 443ms	remaining: 173ms
113:	learn: 0.3650063	total: 447ms	remaining: 169ms
114:	learn: 0.3645530	total: 450ms	remaining: 164ms
115:	learn: 0.3643560	total: 453ms	remaining: 160ms
116:	learn: 0.3639395	total: 456ms	remaining: 156ms
117:	learn: 0.3633543	total: 459ms	remaining: 152ms
118:	learn: 0.3619695	total: 462ms	remaining: 148ms
119:	learn: 

109:	learn: 0.3710206	total: 386ms	remaining: 165ms
110:	learn: 0.3705063	total: 391ms	remaining: 162ms
111:	learn: 0.3701095	total: 394ms	remaining: 158ms
112:	learn: 0.3696795	total: 398ms	remaining: 155ms
113:	learn: 0.3689866	total: 401ms	remaining: 151ms
114:	learn: 0.3682052	total: 406ms	remaining: 148ms
115:	learn: 0.3664952	total: 410ms	remaining: 145ms
116:	learn: 0.3660024	total: 414ms	remaining: 141ms
117:	learn: 0.3656288	total: 418ms	remaining: 138ms
118:	learn: 0.3642510	total: 422ms	remaining: 135ms
119:	learn: 0.3638152	total: 426ms	remaining: 131ms
120:	learn: 0.3633923	total: 430ms	remaining: 128ms
121:	learn: 0.3630975	total: 434ms	remaining: 125ms
122:	learn: 0.3625281	total: 439ms	remaining: 121ms
123:	learn: 0.3617429	total: 443ms	remaining: 118ms
124:	learn: 0.3612121	total: 447ms	remaining: 114ms
125:	learn: 0.3598508	total: 451ms	remaining: 111ms
126:	learn: 0.3583942	total: 455ms	remaining: 108ms
127:	learn: 0.3575449	total: 459ms	remaining: 104ms
128:	learn: 

In [95]:
pd.DataFrame(model_scores).round(4)

Model Name  Accuracy train  \
0                                  LogisticRegression        0.819900   
1                              DecisionTreeClassifier        0.832200   
2                              RandomForestClassifier        0.833100   
3                                          GaussianNB        0.791100   
4                                         BernoulliNB        0.819500   
5                                  AdaBoostClassifier        0.829400   
6                          GradientBoostingClassifier        0.831200   
7                                       XGBClassifier        0.833100   
8   <catboost.core.CatBoostClassifier object at 0x...        0.832700   
9                                      LGBMClassifier        0.834700   
10                               KNeighborsClassifier        0.850200   
11                           LogisticRegression SMOTE        0.674800   
12                       DecisionTreeClassifier SMOTE        0.736500   
13                       RandomForestClassifier SMOTE        0.749700   
14                                   GaussianNB SMOTE        0.649400   
15                                  BernoulliNB SMOTE        0.666600   
16                           AdaBoostClassifier SMOTE        0.734100   
17                   GradientBoostingClassifier SMOTE        0.731800   
18                                XGBClassifier SMOTE        0.875500   
19  <catboost.core.CatBoostClassifier object at 0x...        0.799200   
20                               LGBMClassifier SMOTE        0.824100   
21                         KNeighborsClassifier SMOTE        0.846600   
22                          LogisticRegression ADASYN        0.646700   
23                      DecisionTreeClassifier ADASYN        0.718500   
24                      RandomForestClassifier ADASYN        0.731200   
25                                  GaussianNB ADASYN        0.580200   
26                                 BernoulliNB ADASYN        0.647000   
27                          AdaBoostClassifier ADASYN        0.722000   
28                  GradientBoostingClassifier ADASYN        0.714300   
29                               XGBClassifier ADASYN        0.876600   
30  <catboost.core.CatBoostClassifier object at 0x...        0.788000   
31                              LGBMClassifier ADASYN        0.812600   
32                        KNeighborsClassifier ADASYN        0.834400   
33                             LogisticRegression ENN        0.798200   
34                         DecisionTreeClassifier ENN        0.857900   
35                         RandomForestClassifier ENN        0.872500   
36                                     GaussianNB ENN        0.765200   
37                                    BernoulliNB ENN        0.780900   
38                             AdaBoostClassifier ENN        0.852000   
39                     GradientBoostingClassifier ENN        0.844500   
40                                  XGBClassifier ENN        0.931300   
41  <catboost.core.CatBoostClassifier object at 0x...        0.887300   
42                                 LGBMClassifier ENN        0.913700   
43                           KNeighborsClassifier ENN        0.976300   
44                     LogisticRegression SMOTE + ENN        0.750600   
45                 DecisionTreeClassifier SMOTE + ENN        0.804600   
46                 RandomForestClassifier SMOTE + ENN        0.811500   
47                             GaussianNB SMOTE + ENN        0.713700   
48                            BernoulliNB SMOTE + ENN        0.739200   
49                     AdaBoostClassifier SMOTE + ENN        0.803000   
50             GradientBoostingClassifier SMOTE + ENN        0.796600   
51                          XGBClassifier SMOTE + ENN        0.925400   
52  <catboost.core.CatBoostClassifier object at 0x...        0.860800   
53                         LGBMClassifier SMOTE + ENN        0.888800   
54                   KNeighb

In [96]:
pd.DataFrame(model_scores).round(4).to_csv('tuned_models4.csv', index = False)